

* [Yi-1.5-9B-Chat](#Yi-1.5-9B-Chat)
* [1998](#1998)
* [1999](#1999)
* [2003](#2003)
* [2000](#2000)
* [2020](#2020)
* [2004](#2004)
* [2009](#2009)
* [2001](#2001)
* [2006](#2006)
* [2002](#2002)
* [2005](#2005)
* [2015](#2015)
* [2012](#2012)
* [2019](#2019)
* [2017](#2017)
* [2007](#2007)
* [2013](#2013)
* [2014](#2014)
* [2016](#2016)
* [2018](#2018)
* [2010](#2010)
* [2011](#2011) 

# Yi-1.5-9B-Chat

In [1]:
!nvcc --version

nvcc: NVIDIA (R) Cuda compiler driver
Copyright (c) 2005-2024 NVIDIA Corporation
Built on Thu_Jun__6_02:18:23_PDT_2024
Cuda compilation tools, release 12.5, V12.5.82
Build cuda_12.5.r12.5/compiler.34385749_0


In [2]:
!nvidia-smi

Mon Jun 30 08:43:24 2025       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 560.35.03              Driver Version: 560.35.03      CUDA Version: 12.6     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  Tesla T4                       Off |   00000000:00:04.0 Off |                    0 |
| N/A   39C    P8              9W /   70W |       1MiB /  15360MiB |      0%      Default |
|                                         |                        |                  N/A |
+-----------------------------------------+-----

In [3]:
import torch
import pandas as pd
import time
import numpy as np
import threading
import subprocess
import pynvml
import os
import shutil
import re
import sys
import zipfile
import gc # For garbage collection and clearing CUDA cache

In [4]:
print(torch.__version__)          # e.g. '2.1.0'
print(torch.cuda.is_available())  # should be True on Kaggle GPU

2.5.1+cu124
True


In [5]:
!pip install hf_xet

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.1/3.1 MB 33.7 MB/s eta 0:00:0000:0100:01


In [6]:
from transformers import AutoTokenizer,AutoConfig, LlamaTokenizer , AutoModelForCausalLM, BitsAndBytesConfig
from huggingface_hub import snapshot_download
from sentence_transformers import SentenceTransformer, util
from nltk.translate.bleu_score import sentence_bleu
from tqdm import tqdm
from accelerate import infer_auto_device_map, init_empty_weights
from IPython.display import FileLink
from pathlib import Path

2025-06-30 08:43:43.160130: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1751273023.372744      31 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1751273023.433774      31 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


In [7]:
print("CUDA available:", torch.cuda.is_available())  # Should be True
print("Number of GPUs:", torch.cuda.device_count())   # Should be 2|

CUDA available: True
Number of GPUs: 2


In [8]:
# --- Paraphrase instruction: Emphasize start immediately and end with **** ---
paraphrase_instruction = '''
ONLY provide a robust and as different as possible paraphrase of the above text.
The paraphrase MUST START IMMEDIATELY with the text itself and MUST END with exactly four caret ^: ^^^^.
DO NOT include any introductory phrases, comments, reasoning, conversational fillers, or any other text before the paraphrase starts.
Any additional text or comments or reasoning must ONLY appear AFTER the final ^^^^ marker.
'''
model_small='YI'
model_full='Yi-1.5-9B-Chat'

In [9]:
def create_master_zip_flat(year):
    year_str = str(year)
    master_zip_path = f"/kaggle/working/{year_str}_{model_small}_ALL_PARAPHRASED.zip"
    base_dir = os.path.join("/kaggle/working", year_str)

    with zipfile.ZipFile(master_zip_path, 'w') as master_zip:
        for root, dirs, files in os.walk(base_dir):
            for file in files:
                if file.startswith("paraphrase_") and file.endswith(".txt"):
                    full_path = os.path.join(root, file)

                    # Extract CIK from the path (immediately after the year folder)
                    rel_parts = os.path.relpath(full_path, base_dir).split(os.sep)
                    if len(rel_parts) >= 2:
                        cik = rel_parts[0]
                        arcname = os.path.join(cik, file)
                        master_zip.write(full_path, arcname=arcname)

    print(f"✅ Master ZIP created with flat structure: {master_zip_path}")
    return master_zip_path

# 1998

In [ ]:
year=1998

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'yi_model' in locals() and yi_model is not None:
    del yi_model
    del yi_tokenizer
    print("Yi model and tokenizer objects deleted.")

# 2. Explicitly run Python's garbage collector
# This forces Python to reclaim memory from deleted objects
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
# This is crucial for freeing up unused GPU memory that PyTorch might have reserved
torch.cuda.empty_cache()
print("CUDA cache emptied.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced_yi = {
    'model.embed_tokens': 0, # Keep on GPU0
}


for i in range(22): 
    device_map_balanced_yi[f'model.layers.{i}'] = 0


for i in range(22, 48): 
    device_map_balanced_yi[f'model.layers.{i}'] = 1

device_map_balanced_yi.update({
    'model.norm': 1,
    'model.rotary_emb': 1, # Assuming Yi uses a rotary_emb module similar to Llama/DeepSeek
    'lm_head': 1,
})


# --- Model and Tokenizer Names for Yi-1.5-9B-Chat ---
yi_model_name = "01-ai/Yi-1.5-9B-Chat"

# Step 1: Load config for Yi
yi_config = AutoConfig.from_pretrained(yi_model_name)

# Step 2: Initialize empty model (using the corrected config which is now for 48 layers)
with init_empty_weights():
    yi_model = AutoModelForCausalLM.from_config(yi_config)

# Use the specific device map for Yi
yi_device_map = device_map_balanced_yi

# Step 3: Load pretrained weights with device_map
print(f"Loading {yi_model_name} with torch_dtype=torch.float16 and custom device_map...")
print(f"Device Map being used: {yi_device_map}")
yi_model = AutoModelForCausalLM.from_pretrained(
    yi_model_name,
    device_map=yi_device_map,
    torch_dtype=torch.float16, # Explicitly using float16 as requested
    low_cpu_mem_usage=True # Helps manage memory during loading
)
print(f"{yi_model_name} loaded successfully across GPUs.")

In [ ]:

# --- Load the tokenizer for the Yi model ---
# This assumes 'yi_model_name' is defined earlier, e.g., yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_tokenizer = AutoTokenizer.from_pretrained(yi_model_name)

# Set pad_token_id if it's not defined, crucial for generation
if yi_tokenizer.pad_token_id is None:
    yi_tokenizer.pad_token_id = yi_tokenizer.eos_token_id

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
# --- Paraphrase Function ---
def paraphrase_batch_yi(text_with_prompt, seeds, temps, token_count_input):
    results = []

    messages = [
        {"role": "user", "content": f"Original:\n{text_with_prompt}\n\n{paraphrase_instruction}"},
    ]

    final_yi_prompt = yi_tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        torch.manual_seed(seed)
        inputs = yi_tokenizer(final_yi_prompt, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}

        outputs = yi_model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=yi_tokenizer.eos_token_id,
            pad_token_id=yi_tokenizer.pad_token_id
        )

        decoded = yi_tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")
        paraphrased_text = "ERROR: Pattern not found."

        # Try to capture up to caret (^) first
        match = re.search(r"<\|im_start\|> assistant\s*(.*?)\n\^", decoded, re.DOTALL)
        
        # If caret not found, capture till end
        if not match:
            match = re.search(r"<\|im_start\|> assistant\s*(.*)", decoded, re.DOTALL)
        
        if match:
            paraphrased_text = match.group(1).strip()
            print("Captured text:", paraphrased_text)
        else:
            print("No match found.")
        

        print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
        print(paraphrased_text)
        print(f"--- End MODIFIED OUTPUT for Attempt {i+1}  {model_small} ---\n")
        
        results.append(paraphrased_text)

    return results

In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(yi_tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_yi(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 1999


In [ ]:
year=1999

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'yi_model' in locals() and yi_model is not None:
    del yi_model
    del yi_tokenizer
    print("Yi model and tokenizer objects deleted.")

# 2. Explicitly run Python's garbage collector
# This forces Python to reclaim memory from deleted objects
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
# This is crucial for freeing up unused GPU memory that PyTorch might have reserved
torch.cuda.empty_cache()
print("CUDA cache emptied.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced_yi = {
    'model.embed_tokens': 0, # Keep on GPU0
}


for i in range(22): 
    device_map_balanced_yi[f'model.layers.{i}'] = 0


for i in range(22, 48): 
    device_map_balanced_yi[f'model.layers.{i}'] = 1

device_map_balanced_yi.update({
    'model.norm': 1,
    'model.rotary_emb': 1, # Assuming Yi uses a rotary_emb module similar to Llama/DeepSeek
    'lm_head': 1,
})


# --- Model and Tokenizer Names for Yi-1.5-9B-Chat ---
yi_model_name = "01-ai/Yi-1.5-9B-Chat"

# Step 1: Load config for Yi
yi_config = AutoConfig.from_pretrained(yi_model_name)

# Step 2: Initialize empty model (using the corrected config which is now for 48 layers)
with init_empty_weights():
    yi_model = AutoModelForCausalLM.from_config(yi_config)

# Use the specific device map for Yi
yi_device_map = device_map_balanced_yi

# Step 3: Load pretrained weights with device_map
print(f"Loading {yi_model_name} with torch_dtype=torch.float16 and custom device_map...")
print(f"Device Map being used: {yi_device_map}")
yi_model = AutoModelForCausalLM.from_pretrained(
    yi_model_name,
    device_map=yi_device_map,
    torch_dtype=torch.float16, # Explicitly using float16 as requested
    low_cpu_mem_usage=True # Helps manage memory during loading
)
print(f"{yi_model_name} loaded successfully across GPUs.")

In [ ]:

# --- Load the tokenizer for the Yi model ---
# This assumes 'yi_model_name' is defined earlier, e.g., yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_tokenizer = AutoTokenizer.from_pretrained(yi_model_name)

# Set pad_token_id if it's not defined, crucial for generation
if yi_tokenizer.pad_token_id is None:
    yi_tokenizer.pad_token_id = yi_tokenizer.eos_token_id

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
# --- Paraphrase Function ---
def paraphrase_batch_yi(text_with_prompt, seeds, temps, token_count_input):
    results = []

    messages = [
        {"role": "user", "content": f"Original:\n{text_with_prompt}\n\n{paraphrase_instruction}"},
    ]

    final_yi_prompt = yi_tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        torch.manual_seed(seed)
        inputs = yi_tokenizer(final_yi_prompt, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}

        outputs = yi_model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=yi_tokenizer.eos_token_id,
            pad_token_id=yi_tokenizer.pad_token_id
        )

        decoded = yi_tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")
        print ('------------------------------------------------------')
        print ('\n')
        paraphrased_text = None

       # Step 1: Try matching up to newline followed by caret (\n^)
        match = re.search(r"<\|im_start\|> assistant\s*(.*?)(?:\n\^)", decoded, re.DOTALL)
        
        if match:
            paraphrased_text = match.group(1).strip()
        else:
            # Step 2: No \n^ found — find all carets
            assistant_start = re.search(r"<\|im_start\|> assistant\s*", decoded)
            if assistant_start:
                start_idx = assistant_start.end()
                post_assistant = decoded[start_idx:]
        
                caret_matches = list(re.finditer(r"\^", post_assistant))
        
                if len(caret_matches) >= 2:
                    # Capture text between start and second caret
                    paraphrased_text = post_assistant[:caret_matches[1].start()].strip()
                else:
                    # Step 3: Fallback — capture everything
                    paraphrased_text = post_assistant.strip()
        # Output result
        if paraphrased_text:
            print ('------------------------------------------------------')
            print ('\n')
            print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
            print(paraphrased_text)
            print(f"--- End MODIFIED OUTPUT for Attempt {i+1}  {model_small} ---\n")
            print ('------------------------------------------------------')
            print ('\n')
        else:
            print ('------------------------------------------------------')
            print ('\n')
            print("No match found.")
            print ('------------------------------------------------------')
            print ('\n')
        

        
        
        results.append(paraphrased_text)

    return results

In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(yi_tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_yi(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2003


In [ ]:
year=2003

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'yi_model' in locals() and yi_model is not None:
    del yi_model
    del yi_tokenizer
    print("Yi model and tokenizer objects deleted.")

# 2. Explicitly run Python's garbage collector
# This forces Python to reclaim memory from deleted objects
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
# This is crucial for freeing up unused GPU memory that PyTorch might have reserved
torch.cuda.empty_cache()
print("CUDA cache emptied.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced_yi = {
    'model.embed_tokens': 0, # Keep on GPU0
}


for i in range(22): 
    device_map_balanced_yi[f'model.layers.{i}'] = 0


for i in range(22, 48): 
    device_map_balanced_yi[f'model.layers.{i}'] = 1

device_map_balanced_yi.update({
    'model.norm': 1,
    'model.rotary_emb': 1, # Assuming Yi uses a rotary_emb module similar to Llama/DeepSeek
    'lm_head': 1,
})


# --- Model and Tokenizer Names for Yi-1.5-9B-Chat ---
yi_model_name = "01-ai/Yi-1.5-9B-Chat"

# Step 1: Load config for Yi
yi_config = AutoConfig.from_pretrained(yi_model_name)

# Step 2: Initialize empty model (using the corrected config which is now for 48 layers)
with init_empty_weights():
    yi_model = AutoModelForCausalLM.from_config(yi_config)

# Use the specific device map for Yi
yi_device_map = device_map_balanced_yi

# Step 3: Load pretrained weights with device_map
print(f"Loading {yi_model_name} with torch_dtype=torch.float16 and custom device_map...")
print(f"Device Map being used: {yi_device_map}")
yi_model = AutoModelForCausalLM.from_pretrained(
    yi_model_name,
    device_map=yi_device_map,
    torch_dtype=torch.float16, # Explicitly using float16 as requested
    low_cpu_mem_usage=True # Helps manage memory during loading
)
print(f"{yi_model_name} loaded successfully across GPUs.")

In [ ]:

# --- Load the tokenizer for the Yi model ---
# This assumes 'yi_model_name' is defined earlier, e.g., yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_tokenizer = AutoTokenizer.from_pretrained(yi_model_name)

# Set pad_token_id if it's not defined, crucial for generation
if yi_tokenizer.pad_token_id is None:
    yi_tokenizer.pad_token_id = yi_tokenizer.eos_token_id

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
# --- Paraphrase Function ---
def paraphrase_batch_yi(text_with_prompt, seeds, temps, token_count_input):
    results = []

    messages = [
        {"role": "user", "content": f"Original:\n{text_with_prompt}\n\n{paraphrase_instruction}"},
    ]

    final_yi_prompt = yi_tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        torch.manual_seed(seed)
        inputs = yi_tokenizer(final_yi_prompt, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}

        outputs = yi_model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=yi_tokenizer.eos_token_id,
            pad_token_id=yi_tokenizer.pad_token_id
        )

        decoded = yi_tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")
        print ('------------------------------------------------------')
        print ('\n')
        paraphrased_text = None

       # Step 1: Try matching up to newline followed by caret (\n^)
        match = re.search(r"<\|im_start\|> assistant\s*(.*?)(?:\n\^)", decoded, re.DOTALL)
        
        if match:
            paraphrased_text = match.group(1).strip()
        else:
            # Step 2: No \n^ found — find all carets
            assistant_start = re.search(r"<\|im_start\|> assistant\s*", decoded)
            if assistant_start:
                start_idx = assistant_start.end()
                post_assistant = decoded[start_idx:]
        
                caret_matches = list(re.finditer(r"\^", post_assistant))
        
                if len(caret_matches) >= 2:
                    # Capture text between start and second caret
                    paraphrased_text = post_assistant[:caret_matches[1].start()].strip()
                else:
                    # Step 3: Fallback — capture everything
                    paraphrased_text = post_assistant.strip()
        # Output result
        if paraphrased_text:
            print ('------------------------------------------------------')
            print ('\n')
            print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
            print(paraphrased_text)
            print(f"--- End MODIFIED OUTPUT for Attempt {i+1}  {model_small} ---\n")
            print ('------------------------------------------------------')
            print ('\n')
        else:
            print ('------------------------------------------------------')
            print ('\n')
            print("No match found.")
            print ('------------------------------------------------------')
            print ('\n')
        

        
        
        results.append(paraphrased_text)

    return results

In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(yi_tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_yi(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2000

In [ ]:
year=2000

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'yi_model' in locals() and yi_model is not None:
    del yi_model
    del yi_tokenizer
    print("Yi model and tokenizer objects deleted.")

# 2. Explicitly run Python's garbage collector
# This forces Python to reclaim memory from deleted objects
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
# This is crucial for freeing up unused GPU memory that PyTorch might have reserved
torch.cuda.empty_cache()
print("CUDA cache emptied.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced_yi = {
    'model.embed_tokens': 0, # Keep on GPU0
}


for i in range(22): 
    device_map_balanced_yi[f'model.layers.{i}'] = 0


for i in range(22, 48): 
    device_map_balanced_yi[f'model.layers.{i}'] = 1

device_map_balanced_yi.update({
    'model.norm': 1,
    'model.rotary_emb': 1, # Assuming Yi uses a rotary_emb module similar to Llama/DeepSeek
    'lm_head': 1,
})


# --- Model and Tokenizer Names for Yi-1.5-9B-Chat ---
yi_model_name = "01-ai/Yi-1.5-9B-Chat"

# Step 1: Load config for Yi
yi_config = AutoConfig.from_pretrained(yi_model_name)

# Step 2: Initialize empty model (using the corrected config which is now for 48 layers)
with init_empty_weights():
    yi_model = AutoModelForCausalLM.from_config(yi_config)

# Use the specific device map for Yi
yi_device_map = device_map_balanced_yi

# Step 3: Load pretrained weights with device_map
print(f"Loading {yi_model_name} with torch_dtype=torch.float16 and custom device_map...")
print(f"Device Map being used: {yi_device_map}")
yi_model = AutoModelForCausalLM.from_pretrained(
    yi_model_name,
    device_map=yi_device_map,
    torch_dtype=torch.float16, # Explicitly using float16 as requested
    low_cpu_mem_usage=True # Helps manage memory during loading
)
print(f"{yi_model_name} loaded successfully across GPUs.")

In [ ]:

# --- Load the tokenizer for the Yi model ---
# This assumes 'yi_model_name' is defined earlier, e.g., yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_tokenizer = AutoTokenizer.from_pretrained(yi_model_name)

# Set pad_token_id if it's not defined, crucial for generation
if yi_tokenizer.pad_token_id is None:
    yi_tokenizer.pad_token_id = yi_tokenizer.eos_token_id

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
# --- Paraphrase Function ---
def paraphrase_batch_yi(text_with_prompt, seeds, temps, token_count_input):
    results = []

    messages = [
        {"role": "user", "content": f"Original:\n{text_with_prompt}\n\n{paraphrase_instruction}"},
    ]

    final_yi_prompt = yi_tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        torch.manual_seed(seed)
        inputs = yi_tokenizer(final_yi_prompt, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}

        outputs = yi_model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=yi_tokenizer.eos_token_id,
            pad_token_id=yi_tokenizer.pad_token_id
        )

        decoded = yi_tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")
        print ('------------------------------------------------------')
        print ('\n')
        paraphrased_text = None

       # Step 1: Try matching up to newline followed by caret (\n^)
        match = re.search(r"<\|im_start\|> assistant\s*(.*?)(?:\n\^)", decoded, re.DOTALL)
        
        if match:
            paraphrased_text = match.group(1).strip()
        else:
            # Step 2: No \n^ found — find all carets
            assistant_start = re.search(r"<\|im_start\|> assistant\s*", decoded)
            if assistant_start:
                start_idx = assistant_start.end()
                post_assistant = decoded[start_idx:]
        
                caret_matches = list(re.finditer(r"\^", post_assistant))
        
                if len(caret_matches) >= 2:
                    # Capture text between start and second caret
                    paraphrased_text = post_assistant[:caret_matches[1].start()].strip()
                else:
                    # Step 3: Fallback — capture everything
                    paraphrased_text = post_assistant.strip()
        # Output result
        if paraphrased_text:
            print ('------------------------------------------------------')
            print ('\n')
            print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
            print(paraphrased_text)
            print(f"--- End MODIFIED OUTPUT for Attempt {i+1}  {model_small} ---\n")
            print ('------------------------------------------------------')
            print ('\n')
        else:
            print ('------------------------------------------------------')
            print ('\n')
            print("No match found.")
            print ('------------------------------------------------------')
            print ('\n')
        

        
        
        results.append(paraphrased_text)

    return results

In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(yi_tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_yi(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2020

In [ ]:
year=2020

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'yi_model' in locals() and yi_model is not None:
    del yi_model
    del yi_tokenizer
    print("Yi model and tokenizer objects deleted.")

# 2. Explicitly run Python's garbage collector
# This forces Python to reclaim memory from deleted objects
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
# This is crucial for freeing up unused GPU memory that PyTorch might have reserved
torch.cuda.empty_cache()
print("CUDA cache emptied.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced_yi = {
    'model.embed_tokens': 0, # Keep on GPU0
}


for i in range(22): 
    device_map_balanced_yi[f'model.layers.{i}'] = 0


for i in range(22, 48): 
    device_map_balanced_yi[f'model.layers.{i}'] = 1

device_map_balanced_yi.update({
    'model.norm': 1,
    'model.rotary_emb': 1, # Assuming Yi uses a rotary_emb module similar to Llama/DeepSeek
    'lm_head': 1,
})


# --- Model and Tokenizer Names for Yi-1.5-9B-Chat ---
yi_model_name = "01-ai/Yi-1.5-9B-Chat"

# Step 1: Load config for Yi
yi_config = AutoConfig.from_pretrained(yi_model_name)

# Step 2: Initialize empty model (using the corrected config which is now for 48 layers)
with init_empty_weights():
    yi_model = AutoModelForCausalLM.from_config(yi_config)

# Use the specific device map for Yi
yi_device_map = device_map_balanced_yi

# Step 3: Load pretrained weights with device_map
print(f"Loading {yi_model_name} with torch_dtype=torch.float16 and custom device_map...")
print(f"Device Map being used: {yi_device_map}")
yi_model = AutoModelForCausalLM.from_pretrained(
    yi_model_name,
    device_map=yi_device_map,
    torch_dtype=torch.float16, # Explicitly using float16 as requested
    low_cpu_mem_usage=True # Helps manage memory during loading
)
print(f"{yi_model_name} loaded successfully across GPUs.")

In [ ]:

# --- Load the tokenizer for the Yi model ---
# This assumes 'yi_model_name' is defined earlier, e.g., yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_tokenizer = AutoTokenizer.from_pretrained(yi_model_name)

# Set pad_token_id if it's not defined, crucial for generation
if yi_tokenizer.pad_token_id is None:
    yi_tokenizer.pad_token_id = yi_tokenizer.eos_token_id

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
# --- Paraphrase Function ---
def paraphrase_batch_yi(text_with_prompt, seeds, temps, token_count_input):
    results = []

    messages = [
        {"role": "user", "content": f"Original:\n{text_with_prompt}\n\n{paraphrase_instruction}"},
    ]

    final_yi_prompt = yi_tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        torch.manual_seed(seed)
        inputs = yi_tokenizer(final_yi_prompt, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}

        outputs = yi_model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=yi_tokenizer.eos_token_id,
            pad_token_id=yi_tokenizer.pad_token_id
        )

        decoded = yi_tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")
        print ('------------------------------------------------------')
        print ('\n')
        paraphrased_text = None

       # Step 1: Try matching up to newline followed by caret (\n^)
        match = re.search(r"<\|im_start\|> assistant\s*(.*?)(?:\n\^)", decoded, re.DOTALL)
        
        if match:
            paraphrased_text = match.group(1).strip()
        else:
            # Step 2: No \n^ found — find all carets
            assistant_start = re.search(r"<\|im_start\|> assistant\s*", decoded)
            if assistant_start:
                start_idx = assistant_start.end()
                post_assistant = decoded[start_idx:]
        
                caret_matches = list(re.finditer(r"\^", post_assistant))
        
                if len(caret_matches) >= 2:
                    # Capture text between start and second caret
                    paraphrased_text = post_assistant[:caret_matches[1].start()].strip()
                else:
                    # Step 3: Fallback — capture everything
                    paraphrased_text = post_assistant.strip()
        # Output result
        if paraphrased_text:
            print ('------------------------------------------------------')
            print ('\n')
            print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
            print(paraphrased_text)
            print(f"--- End MODIFIED OUTPUT for Attempt {i+1}  {model_small} ---\n")
            print ('------------------------------------------------------')
            print ('\n')
        else:
            print ('------------------------------------------------------')
            print ('\n')
            print("No match found.")
            print ('------------------------------------------------------')
            print ('\n')
        

        
        
        results.append(paraphrased_text)

    return results

In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(yi_tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_yi(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2008

In [ ]:
year=2008

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'yi_model' in locals() and yi_model is not None:
    del yi_model
    del yi_tokenizer
    print("Yi model and tokenizer objects deleted.")

# 2. Explicitly run Python's garbage collector
# This forces Python to reclaim memory from deleted objects
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
# This is crucial for freeing up unused GPU memory that PyTorch might have reserved
torch.cuda.empty_cache()
print("CUDA cache emptied.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced_yi = {
    'model.embed_tokens': 0, # Keep on GPU0
}


for i in range(22): 
    device_map_balanced_yi[f'model.layers.{i}'] = 0


for i in range(22, 48): 
    device_map_balanced_yi[f'model.layers.{i}'] = 1

device_map_balanced_yi.update({
    'model.norm': 1,
    'model.rotary_emb': 1, # Assuming Yi uses a rotary_emb module similar to Llama/DeepSeek
    'lm_head': 1,
})


# --- Model and Tokenizer Names for Yi-1.5-9B-Chat ---
yi_model_name = "01-ai/Yi-1.5-9B-Chat"

# Step 1: Load config for Yi
yi_config = AutoConfig.from_pretrained(yi_model_name)

# Step 2: Initialize empty model (using the corrected config which is now for 48 layers)
with init_empty_weights():
    yi_model = AutoModelForCausalLM.from_config(yi_config)

# Use the specific device map for Yi
yi_device_map = device_map_balanced_yi

# Step 3: Load pretrained weights with device_map
print(f"Loading {yi_model_name} with torch_dtype=torch.float16 and custom device_map...")
print(f"Device Map being used: {yi_device_map}")
yi_model = AutoModelForCausalLM.from_pretrained(
    yi_model_name,
    device_map=yi_device_map,
    torch_dtype=torch.float16, # Explicitly using float16 as requested
    low_cpu_mem_usage=True # Helps manage memory during loading
)
print(f"{yi_model_name} loaded successfully across GPUs.")

In [ ]:

# --- Load the tokenizer for the Yi model ---
# This assumes 'yi_model_name' is defined earlier, e.g., yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_tokenizer = AutoTokenizer.from_pretrained(yi_model_name)

# Set pad_token_id if it's not defined, crucial for generation
if yi_tokenizer.pad_token_id is None:
    yi_tokenizer.pad_token_id = yi_tokenizer.eos_token_id

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
# --- Paraphrase Function ---
def paraphrase_batch_yi(text_with_prompt, seeds, temps, token_count_input):
    results = []

    messages = [
        {"role": "user", "content": f"Original:\n{text_with_prompt}\n\n{paraphrase_instruction}"},
    ]

    final_yi_prompt = yi_tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        torch.manual_seed(seed)
        inputs = yi_tokenizer(final_yi_prompt, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}

        outputs = yi_model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=yi_tokenizer.eos_token_id,
            pad_token_id=yi_tokenizer.pad_token_id
        )

        decoded = yi_tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")
        print ('------------------------------------------------------')
        print ('\n')
        paraphrased_text = None

       # Step 1: Try matching up to newline followed by caret (\n^)
        match = re.search(r"<\|im_start\|> assistant\s*(.*?)(?:\n\^)", decoded, re.DOTALL)
        
        if match:
            paraphrased_text = match.group(1).strip()
        else:
            # Step 2: No \n^ found — find all carets
            assistant_start = re.search(r"<\|im_start\|> assistant\s*", decoded)
            if assistant_start:
                start_idx = assistant_start.end()
                post_assistant = decoded[start_idx:]
        
                caret_matches = list(re.finditer(r"\^", post_assistant))
        
                if len(caret_matches) >= 2:
                    # Capture text between start and second caret
                    paraphrased_text = post_assistant[:caret_matches[1].start()].strip()
                else:
                    # Step 3: Fallback — capture everything
                    paraphrased_text = post_assistant.strip()
        # Output result
        if paraphrased_text:
            print ('------------------------------------------------------')
            print ('\n')
            print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
            print(paraphrased_text)
            print(f"--- End MODIFIED OUTPUT for Attempt {i+1}  {model_small} ---\n")
            print ('------------------------------------------------------')
            print ('\n')
        else:
            print ('------------------------------------------------------')
            print ('\n')
            print("No match found.")
            print ('------------------------------------------------------')
            print ('\n')
        

        
        
        results.append(paraphrased_text)

    return results

In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(yi_tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_yi(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2004

In [ ]:
year=2004

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'yi_model' in locals() and yi_model is not None:
    del yi_model
    del yi_tokenizer
    print("Yi model and tokenizer objects deleted.")

# 2. Explicitly run Python's garbage collector
# This forces Python to reclaim memory from deleted objects
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
# This is crucial for freeing up unused GPU memory that PyTorch might have reserved
torch.cuda.empty_cache()
print("CUDA cache emptied.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced_yi = {
    'model.embed_tokens': 0, # Keep on GPU0
}


for i in range(22): 
    device_map_balanced_yi[f'model.layers.{i}'] = 0


for i in range(22, 48): 
    device_map_balanced_yi[f'model.layers.{i}'] = 1

device_map_balanced_yi.update({
    'model.norm': 1,
    'model.rotary_emb': 1, # Assuming Yi uses a rotary_emb module similar to Llama/DeepSeek
    'lm_head': 1,
})


# --- Model and Tokenizer Names for Yi-1.5-9B-Chat ---
yi_model_name = "01-ai/Yi-1.5-9B-Chat"

# Step 1: Load config for Yi
yi_config = AutoConfig.from_pretrained(yi_model_name)

# Step 2: Initialize empty model (using the corrected config which is now for 48 layers)
with init_empty_weights():
    yi_model = AutoModelForCausalLM.from_config(yi_config)

# Use the specific device map for Yi
yi_device_map = device_map_balanced_yi

# Step 3: Load pretrained weights with device_map
print(f"Loading {yi_model_name} with torch_dtype=torch.float16 and custom device_map...")
print(f"Device Map being used: {yi_device_map}")
yi_model = AutoModelForCausalLM.from_pretrained(
    yi_model_name,
    device_map=yi_device_map,
    torch_dtype=torch.float16, # Explicitly using float16 as requested
    low_cpu_mem_usage=True # Helps manage memory during loading
)
print(f"{yi_model_name} loaded successfully across GPUs.")

In [ ]:

# --- Load the tokenizer for the Yi model ---
# This assumes 'yi_model_name' is defined earlier, e.g., yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_tokenizer = AutoTokenizer.from_pretrained(yi_model_name)

# Set pad_token_id if it's not defined, crucial for generation
if yi_tokenizer.pad_token_id is None:
    yi_tokenizer.pad_token_id = yi_tokenizer.eos_token_id

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
# --- Paraphrase Function ---
def paraphrase_batch_yi(text_with_prompt, seeds, temps, token_count_input):
    results = []

    messages = [
        {"role": "user", "content": f"Original:\n{text_with_prompt}\n\n{paraphrase_instruction}"},
    ]

    final_yi_prompt = yi_tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        torch.manual_seed(seed)
        inputs = yi_tokenizer(final_yi_prompt, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}

        outputs = yi_model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=yi_tokenizer.eos_token_id,
            pad_token_id=yi_tokenizer.pad_token_id
        )

        decoded = yi_tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")
        print ('------------------------------------------------------')
        print ('\n')
        paraphrased_text = None

       # Step 1: Try matching up to newline followed by caret (\n^)
        match = re.search(r"<\|im_start\|> assistant\s*(.*?)(?:\n\^)", decoded, re.DOTALL)
        
        if match:
            paraphrased_text = match.group(1).strip()
        else:
            # Step 2: No \n^ found — find all carets
            assistant_start = re.search(r"<\|im_start\|> assistant\s*", decoded)
            if assistant_start:
                start_idx = assistant_start.end()
                post_assistant = decoded[start_idx:]
        
                caret_matches = list(re.finditer(r"\^", post_assistant))
        
                if len(caret_matches) >= 2:
                    # Capture text between start and second caret
                    paraphrased_text = post_assistant[:caret_matches[1].start()].strip()
                else:
                    # Step 3: Fallback — capture everything
                    paraphrased_text = post_assistant.strip()
        # Output result
        if paraphrased_text:
            print ('------------------------------------------------------')
            print ('\n')
            print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
            print(paraphrased_text)
            print(f"--- End MODIFIED OUTPUT for Attempt {i+1}  {model_small} ---\n")
            print ('------------------------------------------------------')
            print ('\n')
        else:
            print ('------------------------------------------------------')
            print ('\n')
            print("No match found.")
            print ('------------------------------------------------------')
            print ('\n')
        

        
        
        results.append(paraphrased_text)

    return results

In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(yi_tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_yi(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2009

In [ ]:
year=2009

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'yi_model' in locals() and yi_model is not None:
    del yi_model
    del yi_tokenizer
    print("Yi model and tokenizer objects deleted.")

# 2. Explicitly run Python's garbage collector
# This forces Python to reclaim memory from deleted objects
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
# This is crucial for freeing up unused GPU memory that PyTorch might have reserved
torch.cuda.empty_cache()
print("CUDA cache emptied.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced_yi = {
    'model.embed_tokens': 0, # Keep on GPU0
}


for i in range(22): 
    device_map_balanced_yi[f'model.layers.{i}'] = 0


for i in range(22, 48): 
    device_map_balanced_yi[f'model.layers.{i}'] = 1

device_map_balanced_yi.update({
    'model.norm': 1,
    'model.rotary_emb': 1, # Assuming Yi uses a rotary_emb module similar to Llama/DeepSeek
    'lm_head': 1,
})


# --- Model and Tokenizer Names for Yi-1.5-9B-Chat ---
yi_model_name = "01-ai/Yi-1.5-9B-Chat"

# Step 1: Load config for Yi
yi_config = AutoConfig.from_pretrained(yi_model_name)

# Step 2: Initialize empty model (using the corrected config which is now for 48 layers)
with init_empty_weights():
    yi_model = AutoModelForCausalLM.from_config(yi_config)

# Use the specific device map for Yi
yi_device_map = device_map_balanced_yi

# Step 3: Load pretrained weights with device_map
print(f"Loading {yi_model_name} with torch_dtype=torch.float16 and custom device_map...")
print(f"Device Map being used: {yi_device_map}")
yi_model = AutoModelForCausalLM.from_pretrained(
    yi_model_name,
    device_map=yi_device_map,
    torch_dtype=torch.float16, # Explicitly using float16 as requested
    low_cpu_mem_usage=True # Helps manage memory during loading
)
print(f"{yi_model_name} loaded successfully across GPUs.")

In [ ]:

# --- Load the tokenizer for the Yi model ---
# This assumes 'yi_model_name' is defined earlier, e.g., yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_tokenizer = AutoTokenizer.from_pretrained(yi_model_name)

# Set pad_token_id if it's not defined, crucial for generation
if yi_tokenizer.pad_token_id is None:
    yi_tokenizer.pad_token_id = yi_tokenizer.eos_token_id

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
# --- Paraphrase Function ---
def paraphrase_batch_yi(text_with_prompt, seeds, temps, token_count_input):
    results = []

    messages = [
        {"role": "user", "content": f"Original:\n{text_with_prompt}\n\n{paraphrase_instruction}"},
    ]

    final_yi_prompt = yi_tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        torch.manual_seed(seed)
        inputs = yi_tokenizer(final_yi_prompt, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}

        outputs = yi_model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=yi_tokenizer.eos_token_id,
            pad_token_id=yi_tokenizer.pad_token_id
        )

        decoded = yi_tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")
        print ('------------------------------------------------------')
        print ('\n')
        paraphrased_text = None

       # Step 1: Try matching up to newline followed by caret (\n^)
        match = re.search(r"<\|im_start\|> assistant\s*(.*?)(?:\n\^)", decoded, re.DOTALL)
        
        if match:
            paraphrased_text = match.group(1).strip()
        else:
            # Step 2: No \n^ found — find all carets
            assistant_start = re.search(r"<\|im_start\|> assistant\s*", decoded)
            if assistant_start:
                start_idx = assistant_start.end()
                post_assistant = decoded[start_idx:]
        
                caret_matches = list(re.finditer(r"\^", post_assistant))
        
                if len(caret_matches) >= 2:
                    # Capture text between start and second caret
                    paraphrased_text = post_assistant[:caret_matches[1].start()].strip()
                else:
                    # Step 3: Fallback — capture everything
                    paraphrased_text = post_assistant.strip()
        # Output result
        if paraphrased_text:
            print ('------------------------------------------------------')
            print ('\n')
            print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
            print(paraphrased_text)
            print(f"--- End MODIFIED OUTPUT for Attempt {i+1}  {model_small} ---\n")
            print ('------------------------------------------------------')
            print ('\n')
        else:
            print ('------------------------------------------------------')
            print ('\n')
            print("No match found.")
            print ('------------------------------------------------------')
            print ('\n')
        

        
        
        results.append(paraphrased_text)

    return results

In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(yi_tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_yi(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2001

In [ ]:
year=2001


In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'yi_model' in locals() and yi_model is not None:
    del yi_model
    del yi_tokenizer
    print("Yi model and tokenizer objects deleted.")

# 2. Explicitly run Python's garbage collector
# This forces Python to reclaim memory from deleted objects
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
# This is crucial for freeing up unused GPU memory that PyTorch might have reserved
torch.cuda.empty_cache()
print("CUDA cache emptied.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced_yi = {
    'model.embed_tokens': 0, # Keep on GPU0
}


for i in range(22): 
    device_map_balanced_yi[f'model.layers.{i}'] = 0


for i in range(22, 48): 
    device_map_balanced_yi[f'model.layers.{i}'] = 1

device_map_balanced_yi.update({
    'model.norm': 1,
    'model.rotary_emb': 1, # Assuming Yi uses a rotary_emb module similar to Llama/DeepSeek
    'lm_head': 1,
})


# --- Model and Tokenizer Names for Yi-1.5-9B-Chat ---
yi_model_name = "01-ai/Yi-1.5-9B-Chat"

# Step 1: Load config for Yi
yi_config = AutoConfig.from_pretrained(yi_model_name)

# Step 2: Initialize empty model (using the corrected config which is now for 48 layers)
with init_empty_weights():
    yi_model = AutoModelForCausalLM.from_config(yi_config)

# Use the specific device map for Yi
yi_device_map = device_map_balanced_yi

# Step 3: Load pretrained weights with device_map
print(f"Loading {yi_model_name} with torch_dtype=torch.float16 and custom device_map...")
print(f"Device Map being used: {yi_device_map}")
yi_model = AutoModelForCausalLM.from_pretrained(
    yi_model_name,
    device_map=yi_device_map,
    torch_dtype=torch.float16, # Explicitly using float16 as requested
    low_cpu_mem_usage=True # Helps manage memory during loading
)
print(f"{yi_model_name} loaded successfully across GPUs.")

In [ ]:

# --- Load the tokenizer for the Yi model ---
# This assumes 'yi_model_name' is defined earlier, e.g., yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_tokenizer = AutoTokenizer.from_pretrained(yi_model_name)

# Set pad_token_id if it's not defined, crucial for generation
if yi_tokenizer.pad_token_id is None:
    yi_tokenizer.pad_token_id = yi_tokenizer.eos_token_id

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
# --- Paraphrase Function ---
def paraphrase_batch_yi(text_with_prompt, seeds, temps, token_count_input):
    results = []

    messages = [
        {"role": "user", "content": f"Original:\n{text_with_prompt}\n\n{paraphrase_instruction}"},
    ]

    final_yi_prompt = yi_tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        torch.manual_seed(seed)
        inputs = yi_tokenizer(final_yi_prompt, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}

        outputs = yi_model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=yi_tokenizer.eos_token_id,
            pad_token_id=yi_tokenizer.pad_token_id
        )

        decoded = yi_tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")
        print ('------------------------------------------------------')
        print ('\n')
        paraphrased_text = None

       # Step 1: Try matching up to newline followed by caret (\n^)
        match = re.search(r"<\|im_start\|> assistant\s*(.*?)(?:\n\^)", decoded, re.DOTALL)
        
        if match:
            paraphrased_text = match.group(1).strip()
        else:
            # Step 2: No \n^ found — find all carets
            assistant_start = re.search(r"<\|im_start\|> assistant\s*", decoded)
            if assistant_start:
                start_idx = assistant_start.end()
                post_assistant = decoded[start_idx:]
        
                caret_matches = list(re.finditer(r"\^", post_assistant))
        
                if len(caret_matches) >= 2:
                    # Capture text between start and second caret
                    paraphrased_text = post_assistant[:caret_matches[1].start()].strip()
                else:
                    # Step 3: Fallback — capture everything
                    paraphrased_text = post_assistant.strip()
        # Output result
        if paraphrased_text:
            print ('------------------------------------------------------')
            print ('\n')
            print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
            print(paraphrased_text)
            print(f"--- End MODIFIED OUTPUT for Attempt {i+1}  {model_small} ---\n")
            print ('------------------------------------------------------')
            print ('\n')
        else:
            print ('------------------------------------------------------')
            print ('\n')
            print("No match found.")
            print ('------------------------------------------------------')
            print ('\n')
        

        
        
        results.append(paraphrased_text)

    return results

In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(yi_tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_yi(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2006

In [ ]:
year=2006


In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'yi_model' in locals() and yi_model is not None:
    del yi_model
    del yi_tokenizer
    print("Yi model and tokenizer objects deleted.")

# 2. Explicitly run Python's garbage collector
# This forces Python to reclaim memory from deleted objects
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
# This is crucial for freeing up unused GPU memory that PyTorch might have reserved
torch.cuda.empty_cache()
print("CUDA cache emptied.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced_yi = {
    'model.embed_tokens': 0, # Keep on GPU0
}


for i in range(22): 
    device_map_balanced_yi[f'model.layers.{i}'] = 0


for i in range(22, 48): 
    device_map_balanced_yi[f'model.layers.{i}'] = 1

device_map_balanced_yi.update({
    'model.norm': 1,
    'model.rotary_emb': 1, # Assuming Yi uses a rotary_emb module similar to Llama/DeepSeek
    'lm_head': 1,
})


# --- Model and Tokenizer Names for Yi-1.5-9B-Chat ---
yi_model_name = "01-ai/Yi-1.5-9B-Chat"

# Step 1: Load config for Yi
yi_config = AutoConfig.from_pretrained(yi_model_name)

# Step 2: Initialize empty model (using the corrected config which is now for 48 layers)
with init_empty_weights():
    yi_model = AutoModelForCausalLM.from_config(yi_config)

# Use the specific device map for Yi
yi_device_map = device_map_balanced_yi

# Step 3: Load pretrained weights with device_map
print(f"Loading {yi_model_name} with torch_dtype=torch.float16 and custom device_map...")
print(f"Device Map being used: {yi_device_map}")
yi_model = AutoModelForCausalLM.from_pretrained(
    yi_model_name,
    device_map=yi_device_map,
    torch_dtype=torch.float16, # Explicitly using float16 as requested
    low_cpu_mem_usage=True # Helps manage memory during loading
)
print(f"{yi_model_name} loaded successfully across GPUs.")

In [ ]:

# --- Load the tokenizer for the Yi model ---
# This assumes 'yi_model_name' is defined earlier, e.g., yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_tokenizer = AutoTokenizer.from_pretrained(yi_model_name)

# Set pad_token_id if it's not defined, crucial for generation
if yi_tokenizer.pad_token_id is None:
    yi_tokenizer.pad_token_id = yi_tokenizer.eos_token_id

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
# --- Paraphrase Function ---
def paraphrase_batch_yi(text_with_prompt, seeds, temps, token_count_input):
    results = []

    messages = [
        {"role": "user", "content": f"Original:\n{text_with_prompt}\n\n{paraphrase_instruction}"},
    ]

    final_yi_prompt = yi_tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        torch.manual_seed(seed)
        inputs = yi_tokenizer(final_yi_prompt, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}

        outputs = yi_model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=yi_tokenizer.eos_token_id,
            pad_token_id=yi_tokenizer.pad_token_id
        )

        decoded = yi_tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")
        print ('------------------------------------------------------')
        print ('\n')
        paraphrased_text = None

       # Step 1: Try matching up to newline followed by caret (\n^)
        match = re.search(r"<\|im_start\|> assistant\s*(.*?)(?:\n\^)", decoded, re.DOTALL)
        
        if match:
            paraphrased_text = match.group(1).strip()
        else:
            # Step 2: No \n^ found — find all carets
            assistant_start = re.search(r"<\|im_start\|> assistant\s*", decoded)
            if assistant_start:
                start_idx = assistant_start.end()
                post_assistant = decoded[start_idx:]
        
                caret_matches = list(re.finditer(r"\^", post_assistant))
        
                if len(caret_matches) >= 2:
                    # Capture text between start and second caret
                    paraphrased_text = post_assistant[:caret_matches[1].start()].strip()
                else:
                    # Step 3: Fallback — capture everything
                    paraphrased_text = post_assistant.strip()
        # Output result
        if paraphrased_text:
            print ('------------------------------------------------------')
            print ('\n')
            print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
            print(paraphrased_text)
            print(f"--- End MODIFIED OUTPUT for Attempt {i+1}  {model_small} ---\n")
            print ('------------------------------------------------------')
            print ('\n')
        else:
            print ('------------------------------------------------------')
            print ('\n')
            print("No match found.")
            print ('------------------------------------------------------')
            print ('\n')
        

        
        
        results.append(paraphrased_text)

    return results

In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path)[12:]:
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(yi_tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_yi(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2002

In [ ]:
year=2002


In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'yi_model' in locals() and yi_model is not None:
    del yi_model
    del yi_tokenizer
    print("Yi model and tokenizer objects deleted.")

# 2. Explicitly run Python's garbage collector
# This forces Python to reclaim memory from deleted objects
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
# This is crucial for freeing up unused GPU memory that PyTorch might have reserved
torch.cuda.empty_cache()
print("CUDA cache emptied.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced_yi = {
    'model.embed_tokens': 0, # Keep on GPU0
}


for i in range(22): 
    device_map_balanced_yi[f'model.layers.{i}'] = 0


for i in range(22, 48): 
    device_map_balanced_yi[f'model.layers.{i}'] = 1

device_map_balanced_yi.update({
    'model.norm': 1,
    'model.rotary_emb': 1, # Assuming Yi uses a rotary_emb module similar to Llama/DeepSeek
    'lm_head': 1,
})


# --- Model and Tokenizer Names for Yi-1.5-9B-Chat ---
yi_model_name = "01-ai/Yi-1.5-9B-Chat"

# Step 1: Load config for Yi
yi_config = AutoConfig.from_pretrained(yi_model_name)

# Step 2: Initialize empty model (using the corrected config which is now for 48 layers)
with init_empty_weights():
    yi_model = AutoModelForCausalLM.from_config(yi_config)

# Use the specific device map for Yi
yi_device_map = device_map_balanced_yi

# Step 3: Load pretrained weights with device_map
print(f"Loading {yi_model_name} with torch_dtype=torch.float16 and custom device_map...")
print(f"Device Map being used: {yi_device_map}")
yi_model = AutoModelForCausalLM.from_pretrained(
    yi_model_name,
    device_map=yi_device_map,
    torch_dtype=torch.float16, # Explicitly using float16 as requested
    low_cpu_mem_usage=True # Helps manage memory during loading
)
print(f"{yi_model_name} loaded successfully across GPUs.")

In [ ]:

# --- Load the tokenizer for the Yi model ---
# This assumes 'yi_model_name' is defined earlier, e.g., yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_tokenizer = AutoTokenizer.from_pretrained(yi_model_name)

# Set pad_token_id if it's not defined, crucial for generation
if yi_tokenizer.pad_token_id is None:
    yi_tokenizer.pad_token_id = yi_tokenizer.eos_token_id

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
# --- Paraphrase Function ---
def paraphrase_batch_yi(text_with_prompt, seeds, temps, token_count_input):
    results = []

    messages = [
        {"role": "user", "content": f"Original:\n{text_with_prompt}\n\n{paraphrase_instruction}"},
    ]

    final_yi_prompt = yi_tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        torch.manual_seed(seed)
        inputs = yi_tokenizer(final_yi_prompt, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}

        outputs = yi_model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=yi_tokenizer.eos_token_id,
            pad_token_id=yi_tokenizer.pad_token_id
        )

        decoded = yi_tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")
        print ('------------------------------------------------------')
        print ('\n')
        paraphrased_text = None

       # Step 1: Try matching up to newline followed by caret (\n^)
        match = re.search(r"<\|im_start\|> assistant\s*(.*?)(?:\n\^)", decoded, re.DOTALL)
        
        if match:
            paraphrased_text = match.group(1).strip()
        else:
            # Step 2: No \n^ found — find all carets
            assistant_start = re.search(r"<\|im_start\|> assistant\s*", decoded)
            if assistant_start:
                start_idx = assistant_start.end()
                post_assistant = decoded[start_idx:]
        
                caret_matches = list(re.finditer(r"\^", post_assistant))
        
                if len(caret_matches) >= 2:
                    # Capture text between start and second caret
                    paraphrased_text = post_assistant[:caret_matches[1].start()].strip()
                else:
                    # Step 3: Fallback — capture everything
                    paraphrased_text = post_assistant.strip()
        # Output result
        if paraphrased_text:
            print ('------------------------------------------------------')
            print ('\n')
            print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
            print(paraphrased_text)
            print(f"--- End MODIFIED OUTPUT for Attempt {i+1}  {model_small} ---\n")
            print ('------------------------------------------------------')
            print ('\n')
        else:
            print ('------------------------------------------------------')
            print ('\n')
            print("No match found.")
            print ('------------------------------------------------------')
            print ('\n')
        

        
        
        results.append(paraphrased_text)

    return results

In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(yi_tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_yi(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2005

In [ ]:
year=2005


In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'yi_model' in locals() and yi_model is not None:
    del yi_model
    del yi_tokenizer
    print("Yi model and tokenizer objects deleted.")

# 2. Explicitly run Python's garbage collector
# This forces Python to reclaim memory from deleted objects
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
# This is crucial for freeing up unused GPU memory that PyTorch might have reserved
torch.cuda.empty_cache()
print("CUDA cache emptied.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced_yi = {
    'model.embed_tokens': 0, # Keep on GPU0
}


for i in range(22): 
    device_map_balanced_yi[f'model.layers.{i}'] = 0


for i in range(22, 48): 
    device_map_balanced_yi[f'model.layers.{i}'] = 1

device_map_balanced_yi.update({
    'model.norm': 1,
    'model.rotary_emb': 1, # Assuming Yi uses a rotary_emb module similar to Llama/DeepSeek
    'lm_head': 1,
})


# --- Model and Tokenizer Names for Yi-1.5-9B-Chat ---
yi_model_name = "01-ai/Yi-1.5-9B-Chat"

# Step 1: Load config for Yi
yi_config = AutoConfig.from_pretrained(yi_model_name)

# Step 2: Initialize empty model (using the corrected config which is now for 48 layers)
with init_empty_weights():
    yi_model = AutoModelForCausalLM.from_config(yi_config)

# Use the specific device map for Yi
yi_device_map = device_map_balanced_yi

# Step 3: Load pretrained weights with device_map
print(f"Loading {yi_model_name} with torch_dtype=torch.float16 and custom device_map...")
print(f"Device Map being used: {yi_device_map}")
yi_model = AutoModelForCausalLM.from_pretrained(
    yi_model_name,
    device_map=yi_device_map,
    torch_dtype=torch.float16, # Explicitly using float16 as requested
    low_cpu_mem_usage=True # Helps manage memory during loading
)
print(f"{yi_model_name} loaded successfully across GPUs.")

In [ ]:

# --- Load the tokenizer for the Yi model ---
# This assumes 'yi_model_name' is defined earlier, e.g., yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_tokenizer = AutoTokenizer.from_pretrained(yi_model_name)

# Set pad_token_id if it's not defined, crucial for generation
if yi_tokenizer.pad_token_id is None:
    yi_tokenizer.pad_token_id = yi_tokenizer.eos_token_id

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
# --- Paraphrase Function ---
def paraphrase_batch_yi(text_with_prompt, seeds, temps, token_count_input):
    results = []

    messages = [
        {"role": "user", "content": f"Original:\n{text_with_prompt}\n\n{paraphrase_instruction}"},
    ]

    final_yi_prompt = yi_tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        torch.manual_seed(seed)
        inputs = yi_tokenizer(final_yi_prompt, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}

        outputs = yi_model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=yi_tokenizer.eos_token_id,
            pad_token_id=yi_tokenizer.pad_token_id
        )

        decoded = yi_tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")
        print ('------------------------------------------------------')
        print ('\n')
        paraphrased_text = None

       # Step 1: Try matching up to newline followed by caret (\n^)
        match = re.search(r"<\|im_start\|> assistant\s*(.*?)(?:\n\^)", decoded, re.DOTALL)
        
        if match:
            paraphrased_text = match.group(1).strip()
        else:
            # Step 2: No \n^ found — find all carets
            assistant_start = re.search(r"<\|im_start\|> assistant\s*", decoded)
            if assistant_start:
                start_idx = assistant_start.end()
                post_assistant = decoded[start_idx:]
        
                caret_matches = list(re.finditer(r"\^", post_assistant))
        
                if len(caret_matches) >= 2:
                    # Capture text between start and second caret
                    paraphrased_text = post_assistant[:caret_matches[1].start()].strip()
                else:
                    # Step 3: Fallback — capture everything
                    paraphrased_text = post_assistant.strip()
        # Output result
        if paraphrased_text:
            print ('------------------------------------------------------')
            print ('\n')
            print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
            print(paraphrased_text)
            print(f"--- End MODIFIED OUTPUT for Attempt {i+1}  {model_small} ---\n")
            print ('------------------------------------------------------')
            print ('\n')
        else:
            print ('------------------------------------------------------')
            print ('\n')
            print("No match found.")
            print ('------------------------------------------------------')
            print ('\n')
        

        
        
        results.append(paraphrased_text)

    return results

In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(yi_tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_yi(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2015

In [ ]:
year=2015

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'yi_model' in locals() and yi_model is not None:
    del yi_model
    del yi_tokenizer
    print("Yi model and tokenizer objects deleted.")

# 2. Explicitly run Python's garbage collector
# This forces Python to reclaim memory from deleted objects
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
# This is crucial for freeing up unused GPU memory that PyTorch might have reserved
torch.cuda.empty_cache()
print("CUDA cache emptied.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced_yi = {
    'model.embed_tokens': 0, # Keep on GPU0
}


for i in range(22): 
    device_map_balanced_yi[f'model.layers.{i}'] = 0


for i in range(22, 48): 
    device_map_balanced_yi[f'model.layers.{i}'] = 1

device_map_balanced_yi.update({
    'model.norm': 1,
    'model.rotary_emb': 1, # Assuming Yi uses a rotary_emb module similar to Llama/DeepSeek
    'lm_head': 1,
})


# --- Model and Tokenizer Names for Yi-1.5-9B-Chat ---
yi_model_name = "01-ai/Yi-1.5-9B-Chat"

# Step 1: Load config for Yi
yi_config = AutoConfig.from_pretrained(yi_model_name)

# Step 2: Initialize empty model (using the corrected config which is now for 48 layers)
with init_empty_weights():
    yi_model = AutoModelForCausalLM.from_config(yi_config)

# Use the specific device map for Yi
yi_device_map = device_map_balanced_yi

# Step 3: Load pretrained weights with device_map
print(f"Loading {yi_model_name} with torch_dtype=torch.float16 and custom device_map...")
print(f"Device Map being used: {yi_device_map}")
yi_model = AutoModelForCausalLM.from_pretrained(
    yi_model_name,
    device_map=yi_device_map,
    torch_dtype=torch.float16, # Explicitly using float16 as requested
    low_cpu_mem_usage=True # Helps manage memory during loading
)
print(f"{yi_model_name} loaded successfully across GPUs.")

In [ ]:

# --- Load the tokenizer for the Yi model ---
# This assumes 'yi_model_name' is defined earlier, e.g., yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_tokenizer = AutoTokenizer.from_pretrained(yi_model_name)

# Set pad_token_id if it's not defined, crucial for generation
if yi_tokenizer.pad_token_id is None:
    yi_tokenizer.pad_token_id = yi_tokenizer.eos_token_id

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
# --- Paraphrase Function ---
def paraphrase_batch_yi(text_with_prompt, seeds, temps, token_count_input):
    results = []

    messages = [
        {"role": "user", "content": f"Original:\n{text_with_prompt}\n\n{paraphrase_instruction}"},
    ]

    final_yi_prompt = yi_tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        torch.manual_seed(seed)
        inputs = yi_tokenizer(final_yi_prompt, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}

        outputs = yi_model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=yi_tokenizer.eos_token_id,
            pad_token_id=yi_tokenizer.pad_token_id
        )

        decoded = yi_tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")
        print ('------------------------------------------------------')
        print ('\n')
        paraphrased_text = None

       # Step 1: Try matching up to newline followed by caret (\n^)
        match = re.search(r"<\|im_start\|> assistant\s*(.*?)(?:\n\^)", decoded, re.DOTALL)
        
        if match:
            paraphrased_text = match.group(1).strip()
        else:
            # Step 2: No \n^ found — find all carets
            assistant_start = re.search(r"<\|im_start\|> assistant\s*", decoded)
            if assistant_start:
                start_idx = assistant_start.end()
                post_assistant = decoded[start_idx:]
        
                caret_matches = list(re.finditer(r"\^", post_assistant))
        
                if len(caret_matches) >= 2:
                    # Capture text between start and second caret
                    paraphrased_text = post_assistant[:caret_matches[1].start()].strip()
                else:
                    # Step 3: Fallback — capture everything
                    paraphrased_text = post_assistant.strip()
        # Output result
        if paraphrased_text:
            print ('------------------------------------------------------')
            print ('\n')
            print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
            print(paraphrased_text)
            print(f"--- End MODIFIED OUTPUT for Attempt {i+1}  {model_small} ---\n")
            print ('------------------------------------------------------')
            print ('\n')
        else:
            print ('------------------------------------------------------')
            print ('\n')
            print("No match found.")
            print ('------------------------------------------------------')
            print ('\n')
        

        
        
        results.append(paraphrased_text)

    return results

In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path)[17:]:
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(yi_tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_yi(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2012

In [ ]:
year=2012

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'yi_model' in locals() and yi_model is not None:
    del yi_model
    del yi_tokenizer
    print("Yi model and tokenizer objects deleted.")

# 2. Explicitly run Python's garbage collector
# This forces Python to reclaim memory from deleted objects
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
# This is crucial for freeing up unused GPU memory that PyTorch might have reserved
torch.cuda.empty_cache()
print("CUDA cache emptied.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced_yi = {
    'model.embed_tokens': 0, # Keep on GPU0
}


for i in range(22): 
    device_map_balanced_yi[f'model.layers.{i}'] = 0


for i in range(22, 48): 
    device_map_balanced_yi[f'model.layers.{i}'] = 1

device_map_balanced_yi.update({
    'model.norm': 1,
    'model.rotary_emb': 1, # Assuming Yi uses a rotary_emb module similar to Llama/DeepSeek
    'lm_head': 1,
})


# --- Model and Tokenizer Names for Yi-1.5-9B-Chat ---
yi_model_name = "01-ai/Yi-1.5-9B-Chat"

# Step 1: Load config for Yi
yi_config = AutoConfig.from_pretrained(yi_model_name)

# Step 2: Initialize empty model (using the corrected config which is now for 48 layers)
with init_empty_weights():
    yi_model = AutoModelForCausalLM.from_config(yi_config)

# Use the specific device map for Yi
yi_device_map = device_map_balanced_yi

# Step 3: Load pretrained weights with device_map
print(f"Loading {yi_model_name} with torch_dtype=torch.float16 and custom device_map...")
print(f"Device Map being used: {yi_device_map}")
yi_model = AutoModelForCausalLM.from_pretrained(
    yi_model_name,
    device_map=yi_device_map,
    torch_dtype=torch.float16, # Explicitly using float16 as requested
    low_cpu_mem_usage=True # Helps manage memory during loading
)
print(f"{yi_model_name} loaded successfully across GPUs.")

In [ ]:

# --- Load the tokenizer for the Yi model ---
# This assumes 'yi_model_name' is defined earlier, e.g., yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_tokenizer = AutoTokenizer.from_pretrained(yi_model_name)

# Set pad_token_id if it's not defined, crucial for generation
if yi_tokenizer.pad_token_id is None:
    yi_tokenizer.pad_token_id = yi_tokenizer.eos_token_id

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
# --- Paraphrase Function ---
def paraphrase_batch_yi(text_with_prompt, seeds, temps, token_count_input):
    results = []

    messages = [
        {"role": "user", "content": f"Original:\n{text_with_prompt}\n\n{paraphrase_instruction}"},
    ]

    final_yi_prompt = yi_tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        torch.manual_seed(seed)
        inputs = yi_tokenizer(final_yi_prompt, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}

        outputs = yi_model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=yi_tokenizer.eos_token_id,
            pad_token_id=yi_tokenizer.pad_token_id
        )

        decoded = yi_tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")
        print ('------------------------------------------------------')
        print ('\n')
        paraphrased_text = None

       # Step 1: Try matching up to newline followed by caret (\n^)
        match = re.search(r"<\|im_start\|> assistant\s*(.*?)(?:\n\^)", decoded, re.DOTALL)
        
        if match:
            paraphrased_text = match.group(1).strip()
        else:
            # Step 2: No \n^ found — find all carets
            assistant_start = re.search(r"<\|im_start\|> assistant\s*", decoded)
            if assistant_start:
                start_idx = assistant_start.end()
                post_assistant = decoded[start_idx:]
        
                caret_matches = list(re.finditer(r"\^", post_assistant))
        
                if len(caret_matches) >= 2:
                    # Capture text between start and second caret
                    paraphrased_text = post_assistant[:caret_matches[1].start()].strip()
                else:
                    # Step 3: Fallback — capture everything
                    paraphrased_text = post_assistant.strip()
        # Output result
        if paraphrased_text:
            print ('------------------------------------------------------')
            print ('\n')
            print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
            print(paraphrased_text)
            print(f"--- End MODIFIED OUTPUT for Attempt {i+1}  {model_small} ---\n")
            print ('------------------------------------------------------')
            print ('\n')
        else:
            print ('------------------------------------------------------')
            print ('\n')
            print("No match found.")
            print ('------------------------------------------------------')
            print ('\n')
        

        
        
        results.append(paraphrased_text)

    return results

In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(yi_tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_yi(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2019

In [ ]:
year=2019

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'yi_model' in locals() and yi_model is not None:
    del yi_model
    del yi_tokenizer
    print("Yi model and tokenizer objects deleted.")

# 2. Explicitly run Python's garbage collector
# This forces Python to reclaim memory from deleted objects
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
# This is crucial for freeing up unused GPU memory that PyTorch might have reserved
torch.cuda.empty_cache()
print("CUDA cache emptied.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced_yi = {
    'model.embed_tokens': 0, # Keep on GPU0
}


for i in range(22): 
    device_map_balanced_yi[f'model.layers.{i}'] = 0


for i in range(22, 48): 
    device_map_balanced_yi[f'model.layers.{i}'] = 1

device_map_balanced_yi.update({
    'model.norm': 1,
    'model.rotary_emb': 1, # Assuming Yi uses a rotary_emb module similar to Llama/DeepSeek
    'lm_head': 1,
})


# --- Model and Tokenizer Names for Yi-1.5-9B-Chat ---
yi_model_name = "01-ai/Yi-1.5-9B-Chat"

# Step 1: Load config for Yi
yi_config = AutoConfig.from_pretrained(yi_model_name)

# Step 2: Initialize empty model (using the corrected config which is now for 48 layers)
with init_empty_weights():
    yi_model = AutoModelForCausalLM.from_config(yi_config)

# Use the specific device map for Yi
yi_device_map = device_map_balanced_yi

# Step 3: Load pretrained weights with device_map
print(f"Loading {yi_model_name} with torch_dtype=torch.float16 and custom device_map...")
print(f"Device Map being used: {yi_device_map}")
yi_model = AutoModelForCausalLM.from_pretrained(
    yi_model_name,
    device_map=yi_device_map,
    torch_dtype=torch.float16, # Explicitly using float16 as requested
    low_cpu_mem_usage=True # Helps manage memory during loading
)
print(f"{yi_model_name} loaded successfully across GPUs.")

In [ ]:

# --- Load the tokenizer for the Yi model ---
# This assumes 'yi_model_name' is defined earlier, e.g., yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_tokenizer = AutoTokenizer.from_pretrained(yi_model_name)

# Set pad_token_id if it's not defined, crucial for generation
if yi_tokenizer.pad_token_id is None:
    yi_tokenizer.pad_token_id = yi_tokenizer.eos_token_id

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
# --- Paraphrase Function ---
def paraphrase_batch_yi(text_with_prompt, seeds, temps, token_count_input):
    results = []

    messages = [
        {"role": "user", "content": f"Original:\n{text_with_prompt}\n\n{paraphrase_instruction}"},
    ]

    final_yi_prompt = yi_tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        torch.manual_seed(seed)
        inputs = yi_tokenizer(final_yi_prompt, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}

        outputs = yi_model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=yi_tokenizer.eos_token_id,
            pad_token_id=yi_tokenizer.pad_token_id
        )

        decoded = yi_tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")
        print ('------------------------------------------------------')
        print ('\n')
        paraphrased_text = None

       # Step 1: Try matching up to newline followed by caret (\n^)
        match = re.search(r"<\|im_start\|> assistant\s*(.*?)(?:\n\^)", decoded, re.DOTALL)
        
        if match:
            paraphrased_text = match.group(1).strip()
        else:
            # Step 2: No \n^ found — find all carets
            assistant_start = re.search(r"<\|im_start\|> assistant\s*", decoded)
            if assistant_start:
                start_idx = assistant_start.end()
                post_assistant = decoded[start_idx:]
        
                caret_matches = list(re.finditer(r"\^", post_assistant))
        
                if len(caret_matches) >= 2:
                    # Capture text between start and second caret
                    paraphrased_text = post_assistant[:caret_matches[1].start()].strip()
                else:
                    # Step 3: Fallback — capture everything
                    paraphrased_text = post_assistant.strip()
        # Output result
        if paraphrased_text:
            print ('------------------------------------------------------')
            print ('\n')
            print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
            print(paraphrased_text)
            print(f"--- End MODIFIED OUTPUT for Attempt {i+1}  {model_small} ---\n")
            print ('------------------------------------------------------')
            print ('\n')
        else:
            print ('------------------------------------------------------')
            print ('\n')
            print("No match found.")
            print ('------------------------------------------------------')
            print ('\n')
        

        
        
        results.append(paraphrased_text)

    return results

In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(yi_tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_yi(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2017

In [ ]:
year=2017

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'yi_model' in locals() and yi_model is not None:
    del yi_model
    del yi_tokenizer
    print("Yi model and tokenizer objects deleted.")

# 2. Explicitly run Python's garbage collector
# This forces Python to reclaim memory from deleted objects
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
# This is crucial for freeing up unused GPU memory that PyTorch might have reserved
torch.cuda.empty_cache()
print("CUDA cache emptied.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced_yi = {
    'model.embed_tokens': 0, # Keep on GPU0
}


for i in range(22): 
    device_map_balanced_yi[f'model.layers.{i}'] = 0


for i in range(22, 48): 
    device_map_balanced_yi[f'model.layers.{i}'] = 1

device_map_balanced_yi.update({
    'model.norm': 1,
    'model.rotary_emb': 1, # Assuming Yi uses a rotary_emb module similar to Llama/DeepSeek
    'lm_head': 1,
})


# --- Model and Tokenizer Names for Yi-1.5-9B-Chat ---
yi_model_name = "01-ai/Yi-1.5-9B-Chat"

# Step 1: Load config for Yi
yi_config = AutoConfig.from_pretrained(yi_model_name)

# Step 2: Initialize empty model (using the corrected config which is now for 48 layers)
with init_empty_weights():
    yi_model = AutoModelForCausalLM.from_config(yi_config)

# Use the specific device map for Yi
yi_device_map = device_map_balanced_yi

# Step 3: Load pretrained weights with device_map
print(f"Loading {yi_model_name} with torch_dtype=torch.float16 and custom device_map...")
print(f"Device Map being used: {yi_device_map}")
yi_model = AutoModelForCausalLM.from_pretrained(
    yi_model_name,
    device_map=yi_device_map,
    torch_dtype=torch.float16, # Explicitly using float16 as requested
    low_cpu_mem_usage=True # Helps manage memory during loading
)
print(f"{yi_model_name} loaded successfully across GPUs.")

In [ ]:

# --- Load the tokenizer for the Yi model ---
# This assumes 'yi_model_name' is defined earlier, e.g., yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_tokenizer = AutoTokenizer.from_pretrained(yi_model_name)

# Set pad_token_id if it's not defined, crucial for generation
if yi_tokenizer.pad_token_id is None:
    yi_tokenizer.pad_token_id = yi_tokenizer.eos_token_id

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
# --- Paraphrase Function ---
def paraphrase_batch_yi(text_with_prompt, seeds, temps, token_count_input):
    results = []

    messages = [
        {"role": "user", "content": f"Original:\n{text_with_prompt}\n\n{paraphrase_instruction}"},
    ]

    final_yi_prompt = yi_tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        torch.manual_seed(seed)
        inputs = yi_tokenizer(final_yi_prompt, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}

        outputs = yi_model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=yi_tokenizer.eos_token_id,
            pad_token_id=yi_tokenizer.pad_token_id
        )

        decoded = yi_tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")
        print ('------------------------------------------------------')
        print ('\n')
        paraphrased_text = None

       # Step 1: Try matching up to newline followed by caret (\n^)
        match = re.search(r"<\|im_start\|> assistant\s*(.*?)(?:\n\^)", decoded, re.DOTALL)
        
        if match:
            paraphrased_text = match.group(1).strip()
        else:
            # Step 2: No \n^ found — find all carets
            assistant_start = re.search(r"<\|im_start\|> assistant\s*", decoded)
            if assistant_start:
                start_idx = assistant_start.end()
                post_assistant = decoded[start_idx:]
        
                caret_matches = list(re.finditer(r"\^", post_assistant))
        
                if len(caret_matches) >= 2:
                    # Capture text between start and second caret
                    paraphrased_text = post_assistant[:caret_matches[1].start()].strip()
                else:
                    # Step 3: Fallback — capture everything
                    paraphrased_text = post_assistant.strip()
        # Output result
        if paraphrased_text:
            print ('------------------------------------------------------')
            print ('\n')
            print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
            print(paraphrased_text)
            print(f"--- End MODIFIED OUTPUT for Attempt {i+1}  {model_small} ---\n")
            print ('------------------------------------------------------')
            print ('\n')
        else:
            print ('------------------------------------------------------')
            print ('\n')
            print("No match found.")
            print ('------------------------------------------------------')
            print ('\n')
        

        
        
        results.append(paraphrased_text)

    return results

In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(yi_tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_yi(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2007

In [ ]:
year=2007

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'yi_model' in locals() and yi_model is not None:
    del yi_model
    del yi_tokenizer
    print("Yi model and tokenizer objects deleted.")

# 2. Explicitly run Python's garbage collector
# This forces Python to reclaim memory from deleted objects
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
# This is crucial for freeing up unused GPU memory that PyTorch might have reserved
torch.cuda.empty_cache()
print("CUDA cache emptied.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced_yi = {
    'model.embed_tokens': 0, # Keep on GPU0
}


for i in range(22): 
    device_map_balanced_yi[f'model.layers.{i}'] = 0


for i in range(22, 48): 
    device_map_balanced_yi[f'model.layers.{i}'] = 1

device_map_balanced_yi.update({
    'model.norm': 1,
    'model.rotary_emb': 1, # Assuming Yi uses a rotary_emb module similar to Llama/DeepSeek
    'lm_head': 1,
})


# --- Model and Tokenizer Names for Yi-1.5-9B-Chat ---
yi_model_name = "01-ai/Yi-1.5-9B-Chat"

# Step 1: Load config for Yi
yi_config = AutoConfig.from_pretrained(yi_model_name)

# Step 2: Initialize empty model (using the corrected config which is now for 48 layers)
with init_empty_weights():
    yi_model = AutoModelForCausalLM.from_config(yi_config)

# Use the specific device map for Yi
yi_device_map = device_map_balanced_yi

# Step 3: Load pretrained weights with device_map
print(f"Loading {yi_model_name} with torch_dtype=torch.float16 and custom device_map...")
print(f"Device Map being used: {yi_device_map}")
yi_model = AutoModelForCausalLM.from_pretrained(
    yi_model_name,
    device_map=yi_device_map,
    torch_dtype=torch.float16, # Explicitly using float16 as requested
    low_cpu_mem_usage=True # Helps manage memory during loading
)
print(f"{yi_model_name} loaded successfully across GPUs.")

In [ ]:

# --- Load the tokenizer for the Yi model ---
# This assumes 'yi_model_name' is defined earlier, e.g., yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_tokenizer = AutoTokenizer.from_pretrained(yi_model_name)

# Set pad_token_id if it's not defined, crucial for generation
if yi_tokenizer.pad_token_id is None:
    yi_tokenizer.pad_token_id = yi_tokenizer.eos_token_id

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
# --- Paraphrase Function ---
def paraphrase_batch_yi(text_with_prompt, seeds, temps, token_count_input):
    results = []

    messages = [
        {"role": "user", "content": f"Original:\n{text_with_prompt}\n\n{paraphrase_instruction}"},
    ]

    final_yi_prompt = yi_tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        torch.manual_seed(seed)
        inputs = yi_tokenizer(final_yi_prompt, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}

        outputs = yi_model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=yi_tokenizer.eos_token_id,
            pad_token_id=yi_tokenizer.pad_token_id
        )

        decoded = yi_tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")
        print ('------------------------------------------------------')
        print ('\n')
        paraphrased_text = None

       # Step 1: Try matching up to newline followed by caret (\n^)
        match = re.search(r"<\|im_start\|> assistant\s*(.*?)(?:\n\^)", decoded, re.DOTALL)
        
        if match:
            paraphrased_text = match.group(1).strip()
        else:
            # Step 2: No \n^ found — find all carets
            assistant_start = re.search(r"<\|im_start\|> assistant\s*", decoded)
            if assistant_start:
                start_idx = assistant_start.end()
                post_assistant = decoded[start_idx:]
        
                caret_matches = list(re.finditer(r"\^", post_assistant))
        
                if len(caret_matches) >= 2:
                    # Capture text between start and second caret
                    paraphrased_text = post_assistant[:caret_matches[1].start()].strip()
                else:
                    # Step 3: Fallback — capture everything
                    paraphrased_text = post_assistant.strip()
        # Output result
        if paraphrased_text:
            print ('------------------------------------------------------')
            print ('\n')
            print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
            print(paraphrased_text)
            print(f"--- End MODIFIED OUTPUT for Attempt {i+1}  {model_small} ---\n")
            print ('------------------------------------------------------')
            print ('\n')
        else:
            print ('------------------------------------------------------')
            print ('\n')
            print("No match found.")
            print ('------------------------------------------------------')
            print ('\n')
        

        
        
        results.append(paraphrased_text)

    return results

In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(yi_tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_yi(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2013

In [ ]:
year=2013

In [ ]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

In [ ]:
if 'yi_model' in locals() and yi_model is not None:
    del yi_model
    del yi_tokenizer
    print("Yi model and tokenizer objects deleted.")

# 2. Explicitly run Python's garbage collector
# This forces Python to reclaim memory from deleted objects
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
# This is crucial for freeing up unused GPU memory that PyTorch might have reserved
torch.cuda.empty_cache()
print("CUDA cache emptied.")


In [ ]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [ ]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [ ]:
device_map_balanced_yi = {
    'model.embed_tokens': 0, # Keep on GPU0
}


for i in range(22): 
    device_map_balanced_yi[f'model.layers.{i}'] = 0


for i in range(22, 48): 
    device_map_balanced_yi[f'model.layers.{i}'] = 1

device_map_balanced_yi.update({
    'model.norm': 1,
    'model.rotary_emb': 1, # Assuming Yi uses a rotary_emb module similar to Llama/DeepSeek
    'lm_head': 1,
})


# --- Model and Tokenizer Names for Yi-1.5-9B-Chat ---
yi_model_name = "01-ai/Yi-1.5-9B-Chat"

# Step 1: Load config for Yi
yi_config = AutoConfig.from_pretrained(yi_model_name)

# Step 2: Initialize empty model (using the corrected config which is now for 48 layers)
with init_empty_weights():
    yi_model = AutoModelForCausalLM.from_config(yi_config)

# Use the specific device map for Yi
yi_device_map = device_map_balanced_yi

# Step 3: Load pretrained weights with device_map
print(f"Loading {yi_model_name} with torch_dtype=torch.float16 and custom device_map...")
print(f"Device Map being used: {yi_device_map}")
yi_model = AutoModelForCausalLM.from_pretrained(
    yi_model_name,
    device_map=yi_device_map,
    torch_dtype=torch.float16, # Explicitly using float16 as requested
    low_cpu_mem_usage=True # Helps manage memory during loading
)
print(f"{yi_model_name} loaded successfully across GPUs.")

In [ ]:

# --- Load the tokenizer for the Yi model ---
# This assumes 'yi_model_name' is defined earlier, e.g., yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_tokenizer = AutoTokenizer.from_pretrained(yi_model_name)

# Set pad_token_id if it's not defined, crucial for generation
if yi_tokenizer.pad_token_id is None:
    yi_tokenizer.pad_token_id = yi_tokenizer.eos_token_id

In [ ]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [ ]:
# --- Paraphrase Function ---
def paraphrase_batch_yi(text_with_prompt, seeds, temps, token_count_input):
    results = []

    messages = [
        {"role": "user", "content": f"Original:\n{text_with_prompt}\n\n{paraphrase_instruction}"},
    ]

    final_yi_prompt = yi_tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        torch.manual_seed(seed)
        inputs = yi_tokenizer(final_yi_prompt, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}

        outputs = yi_model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=yi_tokenizer.eos_token_id,
            pad_token_id=yi_tokenizer.pad_token_id
        )

        decoded = yi_tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")
        print ('------------------------------------------------------')
        print ('\n')
        paraphrased_text = None

       # Step 1: Try matching up to newline followed by caret (\n^)
        match = re.search(r"<\|im_start\|> assistant\s*(.*?)(?:\n\^)", decoded, re.DOTALL)
        
        if match:
            paraphrased_text = match.group(1).strip()
        else:
            # Step 2: No \n^ found — find all carets
            assistant_start = re.search(r"<\|im_start\|> assistant\s*", decoded)
            if assistant_start:
                start_idx = assistant_start.end()
                post_assistant = decoded[start_idx:]
        
                caret_matches = list(re.finditer(r"\^", post_assistant))
        
                if len(caret_matches) >= 2:
                    # Capture text between start and second caret
                    paraphrased_text = post_assistant[:caret_matches[1].start()].strip()
                else:
                    # Step 3: Fallback — capture everything
                    paraphrased_text = post_assistant.strip()
        # Output result
        if paraphrased_text:
            print ('------------------------------------------------------')
            print ('\n')
            print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
            print(paraphrased_text)
            print(f"--- End MODIFIED OUTPUT for Attempt {i+1}  {model_small} ---\n")
            print ('------------------------------------------------------')
            print ('\n')
        else:
            print ('------------------------------------------------------')
            print ('\n')
            print("No match found.")
            print ('------------------------------------------------------')
            print ('\n')
        

        
        
        results.append(paraphrased_text)

    return results

In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path)[-5:]:
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(yi_tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_yi(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2014

In [10]:
year=2014

In [11]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

['351817', '1422105', '1335190', '837173', '1159154', '1301063', '1568832', '805305', '1560443', '1421182', '1489137', '1385544', '1330849', '1548691', '1336545', '1037676', '1594590', '1553588', '38079']
---------------------------
351817
----------------------------
Report of Independent Registered Public Accounting Firm  The Board of Directors and Stockholders of Swift Energy Company     We have audited the accompanying consolidated balance sheets of Swift Energy Company and subsidiaries (the Company) as of December 31, 2014 and 2013, and the related consolidated statements of operations, comprehensive income, stockholders' equity and cash flows for each of the three years in the period ended December 31, 2014. These financial statements are the responsibility of the Company's management. Our responsibility is to express an opinion on these financial statements based on our audits.  We conducted our audits in accordance with the standards of the Public Company Accounting Oversight

In [12]:
if 'yi_model' in locals() and yi_model is not None:
    del yi_model
    del yi_tokenizer
    print("Yi model and tokenizer objects deleted.")

# 2. Explicitly run Python's garbage collector
# This forces Python to reclaim memory from deleted objects
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
# This is crucial for freeing up unused GPU memory that PyTorch might have reserved
torch.cuda.empty_cache()
print("CUDA cache emptied.")


Python garbage collector run.
CUDA cache emptied.


In [13]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [14]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [15]:
device_map_balanced_yi = {
    'model.embed_tokens': 0, # Keep on GPU0
}


for i in range(22): 
    device_map_balanced_yi[f'model.layers.{i}'] = 0


for i in range(22, 48): 
    device_map_balanced_yi[f'model.layers.{i}'] = 1

device_map_balanced_yi.update({
    'model.norm': 1,
    'model.rotary_emb': 1, # Assuming Yi uses a rotary_emb module similar to Llama/DeepSeek
    'lm_head': 1,
})


# --- Model and Tokenizer Names for Yi-1.5-9B-Chat ---
yi_model_name = "01-ai/Yi-1.5-9B-Chat"

# Step 1: Load config for Yi
yi_config = AutoConfig.from_pretrained(yi_model_name)

# Step 2: Initialize empty model (using the corrected config which is now for 48 layers)
with init_empty_weights():
    yi_model = AutoModelForCausalLM.from_config(yi_config)

# Use the specific device map for Yi
yi_device_map = device_map_balanced_yi

# Step 3: Load pretrained weights with device_map
print(f"Loading {yi_model_name} with torch_dtype=torch.float16 and custom device_map...")
print(f"Device Map being used: {yi_device_map}")
yi_model = AutoModelForCausalLM.from_pretrained(
    yi_model_name,
    device_map=yi_device_map,
    torch_dtype=torch.float16, # Explicitly using float16 as requested
    low_cpu_mem_usage=True # Helps manage memory during loading
)
print(f"{yi_model_name} loaded successfully across GPUs.")

config.json:   0%|          | 0.00/661 [00:00<?, ?B/s]

Loading 01-ai/Yi-1.5-9B-Chat with torch_dtype=torch.float16 and custom device_map...
Device Map being used: {'model.embed_tokens': 0, 'model.layers.0': 0, 'model.layers.1': 0, 'model.layers.2': 0, 'model.layers.3': 0, 'model.layers.4': 0, 'model.layers.5': 0, 'model.layers.6': 0, 'model.layers.7': 0, 'model.layers.8': 0, 'model.layers.9': 0, 'model.layers.10': 0, 'model.layers.11': 0, 'model.layers.12': 0, 'model.layers.13': 0, 'model.layers.14': 0, 'model.layers.15': 0, 'model.layers.16': 0, 'model.layers.17': 0, 'model.layers.18': 0, 'model.layers.19': 0, 'model.layers.20': 0, 'model.layers.21': 0, 'model.layers.22': 1, 'model.layers.23': 1, 'model.layers.24': 1, 'model.layers.25': 1, 'model.layers.26': 1, 'model.layers.27': 1, 'model.layers.28': 1, 'model.layers.29': 1, 'model.layers.30': 1, 'model.layers.31': 1, 'model.layers.32': 1, 'model.layers.33': 1, 'model.layers.34': 1, 'model.layers.35': 1, 'model.layers.36': 1, 'model.layers.37': 1, 'model.layers.38': 1, 'model.layers.39':

model.safetensors.index.json: 0.00B [00:00, ?B/s]

Fetching 4 files:   0%|          | 0/4 [00:00<?, ?it/s]

model-00002-of-00004.safetensors:   0%|          | 0.00/4.98G [00:00<?, ?B/s]

...

model-00001-of-00004.safetensors:   0%|          | 0.00/4.93G [00:00<?, ?B/s]

model-00003-of-00004.safetensors:   0%|          | 0.00/4.97G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/132 [00:00<?, ?B/s]

01-ai/Yi-1.5-9B-Chat loaded successfully across GPUs.


In [16]:

# --- Load the tokenizer for the Yi model ---
# This assumes 'yi_model_name' is defined earlier, e.g., yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_tokenizer = AutoTokenizer.from_pretrained(yi_model_name)

# Set pad_token_id if it's not defined, crucial for generation
if yi_tokenizer.pad_token_id is None:
    yi_tokenizer.pad_token_id = yi_tokenizer.eos_token_id

tokenizer_config.json: 0.00B [00:00, ?B/s]

tokenizer.model:   0%|          | 0.00/1.03M [00:00<?, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

special_tokens_map.json:   0%|          | 0.00/567 [00:00<?, ?B/s]

In [17]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [18]:
# --- Paraphrase Function ---
def paraphrase_batch_yi(text_with_prompt, seeds, temps, token_count_input):
    results = []

    messages = [
        {"role": "user", "content": f"Original:\n{text_with_prompt}\n\n{paraphrase_instruction}"},
    ]

    final_yi_prompt = yi_tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        torch.manual_seed(seed)
        inputs = yi_tokenizer(final_yi_prompt, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}

        outputs = yi_model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=yi_tokenizer.eos_token_id,
            pad_token_id=yi_tokenizer.pad_token_id
        )

        decoded = yi_tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")
        print ('------------------------------------------------------')
        print ('\n')
        paraphrased_text = None

       # Step 1: Try matching up to newline followed by caret (\n^)
        match = re.search(r"<\|im_start\|> assistant\s*(.*?)(?:\n\^)", decoded, re.DOTALL)
        
        if match:
            paraphrased_text = match.group(1).strip()
        else:
            # Step 2: No \n^ found — find all carets
            assistant_start = re.search(r"<\|im_start\|> assistant\s*", decoded)
            if assistant_start:
                start_idx = assistant_start.end()
                post_assistant = decoded[start_idx:]
        
                caret_matches = list(re.finditer(r"\^", post_assistant))
        
                if len(caret_matches) >= 2:
                    # Capture text between start and second caret
                    paraphrased_text = post_assistant[:caret_matches[1].start()].strip()
                else:
                    # Step 3: Fallback — capture everything
                    paraphrased_text = post_assistant.strip()
        # Output result
        if paraphrased_text:
            print ('------------------------------------------------------')
            print ('\n')
            print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
            print(paraphrased_text)
            print(f"--- End MODIFIED OUTPUT for Attempt {i+1}  {model_small} ---\n")
            print ('------------------------------------------------------')
            print ('\n')
        else:
            print ('------------------------------------------------------')
            print ('\n')
            print("No match found.")
            print ('------------------------------------------------------')
            print ('\n')
        

        
        
        results.append(paraphrased_text)

    return results

In [ ]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(yi_tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_yi(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

GPU Utilization:   0%|          | 0% , GPU0: 0%/7867MB | GPU1: 0%/9187MB


📄 Processing CIK: 351817
----------------------------------------------



CIK NUMBER: 351817



Original AUDIT OPTINION: 
Report of Independent Registered Public Accounting Firm  The Board of Directors and Stockholders of Swift Energy Company     We have audited the accompanying consolidated balance sheets of Swift Energy Company and subsidiaries (the Company) as of December 31, 2014 and 2013, and the related consolidated statements of operations, comprehensive income, stockholders' equity and cash flows for each of the three years in the period ended December 31, 2014. These financial statements are the responsibility of the Company's management. Our responsibility is to express an opinion on these financial statements based on our audits.  We conducted our audits in accordance with the standards of the Public Company Accounting Oversight Board (United States). Those standards require that we plan and perform the audit to obtain reasonable assurance about whether the financial sta

GPU Utilization:   0%|          | 0% , GPU0: 1%/8033MB | GPU1: 21%/9345MB

GPU Utilization:   0%|          | 0% , GPU0: 41%/8033MB | GPU1: 45%/9345MB

GPU Utilization:   0%|          | 0% , GPU0: 36%/8033MB | GPU1: 47%/9345MB

...

GPU Utilization:   0%|          | 0% , GPU0: 52%/8737MB | GPU1: 45%/10087MB

GPU Utilization:   0%|          | 0% , GPU0: 37%/8737MB | GPU1: 62%/10087MB

GPU Utilization:   0%|          | 0% , GPU0: 51%/8737MB | GPU1: 46%/10087MB

GPU Utilization:   0%|          | 0% , GPU0: 36%/8737MB | GPU1: 61%/10087MB

GPU Utilization:   0%|          | 0% , GPU0: 48%/8737MB | GPU1: 45%/10087MB

In [ ]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

# 2016

In [10]:
year=2016

In [11]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

['38984', '1580185', '786110', '1584701', '98222', '1058623', '920321', '1471261', '1499912', '1281922', '1382911', '1396279', '316300', '1040719', '1594590', '868725', '18172', '1403853', '1030749']
---------------------------
38984
----------------------------
REPORT OF INDEPENDENT REGISTERED PUBLIC ACCOUNTING FIRM  To the Board of Directors and Stockholders of  Real Industry, Inc.  We have audited the accompanying consolidated balance sheets of Real Industry, Inc. as of December 31, 2016 and 2015, and the related consolidated statements of operations, comprehensive income (loss), stockholders equity and cash flows for each of the two years in the period ended December 31, 2016. These financial statements are the responsibility of the Companys management. Our responsibility is to express an opinion on these financial statements based on our audits.  We conducted our audits in accordance with the standards of the Public Company Accounting Oversight Board (United States). Those stand

In [13]:
if 'yi_model' in locals() and yi_model is not None:
    del yi_model
    del yi_tokenizer
    print("Yi model and tokenizer objects deleted.")

# 2. Explicitly run Python's garbage collector
# This forces Python to reclaim memory from deleted objects
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
# This is crucial for freeing up unused GPU memory that PyTorch might have reserved
torch.cuda.empty_cache()
print("CUDA cache emptied.")


Python garbage collector run.
CUDA cache emptied.


In [14]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [15]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [16]:
device_map_balanced_yi = {
    'model.embed_tokens': 0, # Keep on GPU0
}


for i in range(22): 
    device_map_balanced_yi[f'model.layers.{i}'] = 0


for i in range(22, 48): 
    device_map_balanced_yi[f'model.layers.{i}'] = 1

device_map_balanced_yi.update({
    'model.norm': 1,
    'model.rotary_emb': 1, # Assuming Yi uses a rotary_emb module similar to Llama/DeepSeek
    'lm_head': 1,
})


# --- Model and Tokenizer Names for Yi-1.5-9B-Chat ---
yi_model_name = "01-ai/Yi-1.5-9B-Chat"

# Step 1: Load config for Yi
yi_config = AutoConfig.from_pretrained(yi_model_name)

# Step 2: Initialize empty model (using the corrected config which is now for 48 layers)
with init_empty_weights():
    yi_model = AutoModelForCausalLM.from_config(yi_config)

# Use the specific device map for Yi
yi_device_map = device_map_balanced_yi

# Step 3: Load pretrained weights with device_map
print(f"Loading {yi_model_name} with torch_dtype=torch.float16 and custom device_map...")
print(f"Device Map being used: {yi_device_map}")
yi_model = AutoModelForCausalLM.from_pretrained(
    yi_model_name,
    device_map=yi_device_map,
    torch_dtype=torch.float16, # Explicitly using float16 as requested
    low_cpu_mem_usage=True # Helps manage memory during loading
)
print(f"{yi_model_name} loaded successfully across GPUs.")

config.json:   0%|          | 0.00/661 [00:00<?, ?B/s]

Loading 01-ai/Yi-1.5-9B-Chat with torch_dtype=torch.float16 and custom device_map...
Device Map being used: {'model.embed_tokens': 0, 'model.layers.0': 0, 'model.layers.1': 0, 'model.layers.2': 0, 'model.layers.3': 0, 'model.layers.4': 0, 'model.layers.5': 0, 'model.layers.6': 0, 'model.layers.7': 0, 'model.layers.8': 0, 'model.layers.9': 0, 'model.layers.10': 0, 'model.layers.11': 0, 'model.layers.12': 0, 'model.layers.13': 0, 'model.layers.14': 0, 'model.layers.15': 0, 'model.layers.16': 0, 'model.layers.17': 0, 'model.layers.18': 0, 'model.layers.19': 0, 'model.layers.20': 0, 'model.layers.21': 0, 'model.layers.22': 1, 'model.layers.23': 1, 'model.layers.24': 1, 'model.layers.25': 1, 'model.layers.26': 1, 'model.layers.27': 1, 'model.layers.28': 1, 'model.layers.29': 1, 'model.layers.30': 1, 'model.layers.31': 1, 'model.layers.32': 1, 'model.layers.33': 1, 'model.layers.34': 1, 'model.layers.35': 1, 'model.layers.36': 1, 'model.layers.37': 1, 'model.layers.38': 1, 'model.layers.39':

model.safetensors.index.json: 0.00B [00:00, ?B/s]

Fetching 4 files:   0%|          | 0/4 [00:00<?, ?it/s]

model-00001-of-00004.safetensors:   0%|          | 0.00/4.93G [00:00<?, ?B/s]

...

model-00003-of-00004.safetensors:   0%|          | 0.00/4.97G [00:00<?, ?B/s]

model-00002-of-00004.safetensors:   0%|          | 0.00/4.98G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/132 [00:00<?, ?B/s]

01-ai/Yi-1.5-9B-Chat loaded successfully across GPUs.


In [17]:

# --- Load the tokenizer for the Yi model ---
# This assumes 'yi_model_name' is defined earlier, e.g., yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_tokenizer = AutoTokenizer.from_pretrained(yi_model_name)

# Set pad_token_id if it's not defined, crucial for generation
if yi_tokenizer.pad_token_id is None:
    yi_tokenizer.pad_token_id = yi_tokenizer.eos_token_id

tokenizer_config.json: 0.00B [00:00, ?B/s]

tokenizer.model:   0%|          | 0.00/1.03M [00:00<?, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

special_tokens_map.json:   0%|          | 0.00/567 [00:00<?, ?B/s]

In [18]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [19]:
# --- Paraphrase Function ---
def paraphrase_batch_yi(text_with_prompt, seeds, temps, token_count_input):
    results = []

    messages = [
        {"role": "user", "content": f"Original:\n{text_with_prompt}\n\n{paraphrase_instruction}"},
    ]

    final_yi_prompt = yi_tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        torch.manual_seed(seed)
        inputs = yi_tokenizer(final_yi_prompt, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}

        outputs = yi_model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=yi_tokenizer.eos_token_id,
            pad_token_id=yi_tokenizer.pad_token_id
        )

        decoded = yi_tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")
        print ('------------------------------------------------------')
        print ('\n')
        paraphrased_text = None

       # Step 1: Try matching up to newline followed by caret (\n^)
        match = re.search(r"<\|im_start\|> assistant\s*(.*?)(?:\n\^)", decoded, re.DOTALL)
        
        if match:
            paraphrased_text = match.group(1).strip()
        else:
            # Step 2: No \n^ found — find all carets
            assistant_start = re.search(r"<\|im_start\|> assistant\s*", decoded)
            if assistant_start:
                start_idx = assistant_start.end()
                post_assistant = decoded[start_idx:]
        
                caret_matches = list(re.finditer(r"\^", post_assistant))
        
                if len(caret_matches) >= 2:
                    # Capture text between start and second caret
                    paraphrased_text = post_assistant[:caret_matches[1].start()].strip()
                else:
                    # Step 3: Fallback — capture everything
                    paraphrased_text = post_assistant.strip()
        # Output result
        if paraphrased_text:
            print ('------------------------------------------------------')
            print ('\n')
            print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
            print(paraphrased_text)
            print(f"--- End MODIFIED OUTPUT for Attempt {i+1}  {model_small} ---\n")
            print ('------------------------------------------------------')
            print ('\n')
        else:
            print ('------------------------------------------------------')
            print ('\n')
            print("No match found.")
            print ('------------------------------------------------------')
            print ('\n')
        

        
        
        results.append(paraphrased_text)

    return results

In [20]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(yi_tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_yi(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

GPU Utilization:   0%|          | 0% , GPU0: 0%/7867MB | GPU1: 0%/9187MB


📄 Processing CIK: 38984
----------------------------------------------



CIK NUMBER: 38984



Original AUDIT OPTINION: 
REPORT OF INDEPENDENT REGISTERED PUBLIC ACCOUNTING FIRM  To the Board of Directors and Stockholders of  Real Industry, Inc.  We have audited the accompanying consolidated balance sheets of Real Industry, Inc. as of December 31, 2016 and 2015, and the related consolidated statements of operations, comprehensive income (loss), stockholders equity and cash flows for each of the two years in the period ended December 31, 2016. These financial statements are the responsibility of the Companys management. Our responsibility is to express an opinion on these financial statements based on our audits.  We conducted our audits in accordance with the standards of the Public Company Accounting Oversight Board (United States). Those standards require that we plan and perform the audit to obtain reasonable assurance about whether the financial statements are free of material mi

GPU Utilization:   0%|          | 0% , GPU0: 36%/8033MB | GPU1: 5%/9345MB

GPU Utilization:   0%|          | 0% , GPU0: 52%/8033MB | GPU1: 47%/9345MB

GPU Utilization:   0%|          | 0% , GPU0: 52%/8041MB | GPU1: 49%/9353MB

...

GPU Utilization:   0%|          | 0% , GPU0: 43%/8913MB | GPU1: 59%/10265MB

GPU Utilization:   0%|          | 0% , GPU0: 50%/8913MB | GPU1: 52%/10265MB

GPU Utilization:   0%|          | 0% , GPU0: 47%/8913MB | GPU1: 47%/10265MB

--- RAW LLM Output for Attempt 6 ---
<|im_start|> user
 Original:
 Report of Independent Registered Public Accounting Firm        The Board of Directors and Stockholders  GulfMark Offshore,  Inc. :     We have audited the accompanying consolidated balance sheets of GulfMark Offshore,  Inc.  and consolidated subsidiaries (the Company) as of December 31,  2016  and 2015,  and the related consolidated statements of operations,  comprehensive income (loss),  stockholders equity,  and cash flows for each of the years in the three-year period ended December 31,  2016.  These consolidated financial statements are the responsibility of the Companys management.  Our responsibility is to express an opinion on these consolidated financial statements based on our audits.      We conducted our audits in accordance with the standards of the Public Company Accounting Oversight Board (United States).  Those standards require that we plan and perform the audit to obtain reasonable assurance about whe

GPU Utilization:   0%|          | 0% , GPU0: 47%/8913MB | GPU1: 47%/10265MB


In [21]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

✅ Master ZIP created with flat structure: /kaggle/working/2016_YI_ALL_PARAPHRASED.zip


/kaggle/working/2016_YI_ALL_PARAPHRASED.zip

# 2018

In [15]:
year=2018

In [16]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

['1282648', '1528837', '2034', '1573166', '1584952', '1735828', '1547638', '708819', '931336', '1603923', '1056386', '1575360', '1056087', '1310067', '1690769', '1441849', '1405073', '1045425', '1461993']
---------------------------
1282648
----------------------------
REPORT OF INDEPENDENT REGISTERED PUBLIC ACCOUNTING FIRM   To the Board of Directors and Stockholders of  Halcón Resources Corporation  Houston, Texas  Opinion on the Financial Statements   We have audited the accompanying consolidated balance sheets of Halcón Resources Corporation and subsidiaries (the "Company") as of December 31, 2018 and 2017 (Successor Company Balance Sheet), the related consolidated statements of operations, shareholders' equity, and cash flows for the year ended December 31, 2018, 2017 and for the period from September 10, 2016 to December 31, 2016 (Successor Company operations) and January 1, 2016 to September 9, 2016 (Predecessor Company operations) and the related notes (collectively referred to

In [17]:
if 'yi_model' in locals() and yi_model is not None:
    del yi_model
    del yi_tokenizer
    print("Yi model and tokenizer objects deleted.")

# 2. Explicitly run Python's garbage collector
# This forces Python to reclaim memory from deleted objects
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
# This is crucial for freeing up unused GPU memory that PyTorch might have reserved
torch.cuda.empty_cache()
print("CUDA cache emptied.")


Python garbage collector run.
CUDA cache emptied.


In [18]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [19]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [20]:
device_map_balanced_yi = {
    'model.embed_tokens': 0, # Keep on GPU0
}


for i in range(22): 
    device_map_balanced_yi[f'model.layers.{i}'] = 0


for i in range(22, 48): 
    device_map_balanced_yi[f'model.layers.{i}'] = 1

device_map_balanced_yi.update({
    'model.norm': 1,
    'model.rotary_emb': 1, # Assuming Yi uses a rotary_emb module similar to Llama/DeepSeek
    'lm_head': 1,
})


# --- Model and Tokenizer Names for Yi-1.5-9B-Chat ---
yi_model_name = "01-ai/Yi-1.5-9B-Chat"

# Step 1: Load config for Yi
yi_config = AutoConfig.from_pretrained(yi_model_name)

# Step 2: Initialize empty model (using the corrected config which is now for 48 layers)
with init_empty_weights():
    yi_model = AutoModelForCausalLM.from_config(yi_config)

# Use the specific device map for Yi
yi_device_map = device_map_balanced_yi

# Step 3: Load pretrained weights with device_map
print(f"Loading {yi_model_name} with torch_dtype=torch.float16 and custom device_map...")
print(f"Device Map being used: {yi_device_map}")
yi_model = AutoModelForCausalLM.from_pretrained(
    yi_model_name,
    device_map=yi_device_map,
    torch_dtype=torch.float16, # Explicitly using float16 as requested
    low_cpu_mem_usage=True # Helps manage memory during loading
)
print(f"{yi_model_name} loaded successfully across GPUs.")

config.json:   0%|          | 0.00/661 [00:00<?, ?B/s]

Loading 01-ai/Yi-1.5-9B-Chat with torch_dtype=torch.float16 and custom device_map...
Device Map being used: {'model.embed_tokens': 0, 'model.layers.0': 0, 'model.layers.1': 0, 'model.layers.2': 0, 'model.layers.3': 0, 'model.layers.4': 0, 'model.layers.5': 0, 'model.layers.6': 0, 'model.layers.7': 0, 'model.layers.8': 0, 'model.layers.9': 0, 'model.layers.10': 0, 'model.layers.11': 0, 'model.layers.12': 0, 'model.layers.13': 0, 'model.layers.14': 0, 'model.layers.15': 0, 'model.layers.16': 0, 'model.layers.17': 0, 'model.layers.18': 0, 'model.layers.19': 0, 'model.layers.20': 0, 'model.layers.21': 0, 'model.layers.22': 1, 'model.layers.23': 1, 'model.layers.24': 1, 'model.layers.25': 1, 'model.layers.26': 1, 'model.layers.27': 1, 'model.layers.28': 1, 'model.layers.29': 1, 'model.layers.30': 1, 'model.layers.31': 1, 'model.layers.32': 1, 'model.layers.33': 1, 'model.layers.34': 1, 'model.layers.35': 1, 'model.layers.36': 1, 'model.layers.37': 1, 'model.layers.38': 1, 'model.layers.39':

model.safetensors.index.json: 0.00B [00:00, ?B/s]

Fetching 4 files:   0%|          | 0/4 [00:00<?, ?it/s]

model-00003-of-00004.safetensors:   0%|          | 0.00/4.97G [00:00<?, ?B/s]

...

model-00004-of-00004.safetensors:   0%|          | 0.00/2.78G [00:00<?, ?B/s]

model-00002-of-00004.safetensors:   0%|          | 0.00/4.98G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/132 [00:00<?, ?B/s]

01-ai/Yi-1.5-9B-Chat loaded successfully across GPUs.


In [21]:

# --- Load the tokenizer for the Yi model ---
# This assumes 'yi_model_name' is defined earlier, e.g., yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_tokenizer = AutoTokenizer.from_pretrained(yi_model_name)

# Set pad_token_id if it's not defined, crucial for generation
if yi_tokenizer.pad_token_id is None:
    yi_tokenizer.pad_token_id = yi_tokenizer.eos_token_id

tokenizer_config.json: 0.00B [00:00, ?B/s]

tokenizer.model:   0%|          | 0.00/1.03M [00:00<?, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

special_tokens_map.json:   0%|          | 0.00/567 [00:00<?, ?B/s]

In [22]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [23]:
# --- Paraphrase Function ---
def paraphrase_batch_yi(text_with_prompt, seeds, temps, token_count_input):
    results = []

    messages = [
        {"role": "user", "content": f"Original:\n{text_with_prompt}\n\n{paraphrase_instruction}"},
    ]

    final_yi_prompt = yi_tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        torch.manual_seed(seed)
        inputs = yi_tokenizer(final_yi_prompt, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}

        outputs = yi_model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=yi_tokenizer.eos_token_id,
            pad_token_id=yi_tokenizer.pad_token_id
        )

        decoded = yi_tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")
        print ('------------------------------------------------------')
        print ('\n')
        paraphrased_text = None

       # Step 1: Try matching up to newline followed by caret (\n^)
        match = re.search(r"<\|im_start\|> assistant\s*(.*?)(?:\n\^)", decoded, re.DOTALL)
        
        if match:
            paraphrased_text = match.group(1).strip()
        else:
            # Step 2: No \n^ found — find all carets
            assistant_start = re.search(r"<\|im_start\|> assistant\s*", decoded)
            if assistant_start:
                start_idx = assistant_start.end()
                post_assistant = decoded[start_idx:]
        
                caret_matches = list(re.finditer(r"\^", post_assistant))
        
                if len(caret_matches) >= 2:
                    # Capture text between start and second caret
                    paraphrased_text = post_assistant[:caret_matches[1].start()].strip()
                else:
                    # Step 3: Fallback — capture everything
                    paraphrased_text = post_assistant.strip()
        # Output result
        if paraphrased_text:
            print ('------------------------------------------------------')
            print ('\n')
            print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
            print(paraphrased_text)
            print(f"--- End MODIFIED OUTPUT for Attempt {i+1}  {model_small} ---\n")
            print ('------------------------------------------------------')
            print ('\n')
        else:
            print ('------------------------------------------------------')
            print ('\n')
            print("No match found.")
            print ('------------------------------------------------------')
            print ('\n')
        

        
        
        results.append(paraphrased_text)

    return results

In [24]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(yi_tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_yi(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

GPU Utilization:   0%|          | 0% , GPU0: 0%/7883MB | GPU1: 0%/9187MB


📄 Processing CIK: 1441849
----------------------------------------------



CIK NUMBER: 1441849



Original AUDIT OPTINION: 
Report of Independent Registered Public Accounting Firm     To the Board of Directors and Shareholders of Cloud Peak Energy Inc.     Opinions on the Financial Statements and Internal Control over Financial Reporting     We have audited the accompanying consolidated balance sheets of Cloud Peak Energy Inc. and its subsidiaries (the Company) as of December 31, 2018 and 2017, and the related consolidated statements of operations and comprehensive income (loss), of equity and of cash flows for each of the three years in the period ended December 31, 2018, including the related notes, and the financial statement schedule of valuation and qualifying accounts for each of the three years in the period ended December 31, 2018, appearing under Item 15(a)(2) (collectively referred to as the consolidated financial statements). We also have audited the Companys internal

GPU Utilization:   0%|          | 0% , GPU0: 0%/8159MB | GPU1: 100%/9461MB

GPU Utilization:   0%|          | 0% , GPU0: 39%/8163MB | GPU1: 57%/9461MB

GPU Utilization:   0%|          | 0% , GPU0: 44%/8163MB | GPU1: 59%/9461MB

...

GPU Utilization:   0%|          | 0% , GPU0: 41%/8947MB | GPU1: 52%/10309MB

GPU Utilization:   0%|          | 0% , GPU0: 44%/8947MB | GPU1: 56%/10309MB

GPU Utilization:   0%|          | 0% , GPU0: 44%/8947MB | GPU1: 57%/10309MB

GPU Utilization:   0%|          | 0% , GPU0: 44%/8947MB | GPU1: 57%/10309MB

--- RAW LLM Output for Attempt 6 ---
<|im_start|> user
 Original:
 REPORT OF INDEPENDENT REGISTERED PUBLIC ACCOUNTING FIRM  To the shareholders and the Board of Directors of Melinta Therapeutics,  Inc.   Opinions on the Financial Statements and Internal Control over Financial Reporting  We have audited the accompanying consolidated balance sheets of Melinta Therapeutics,  Inc.  and subsidiaries (the "Company") as of December 31,  2018  and 2017,  the related consolidated statements of operations,  shareholders' equity,  and cash flows,  for each of the three years in the period ended December 31,  2018,  and the related notes (collectively referred to as the "financial statements").  We also have audited the Companys internal control over financial reporting as of December 31,  2018,  based on criteria established in Internal Control - Integrated Framework (2013 ) issued by the Committee of Sponsoring Organizations of the Treadway Commission (COSO).   In our opinion,  the financial st

In [25]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

✅ Master ZIP created with flat structure: /kaggle/working/2018_YI_ALL_PARAPHRASED.zip


/kaggle/working/2018_YI_ALL_PARAPHRASED.zip

# 2010

In [17]:
year=2010

In [18]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

['821483', '1283552', '1397867', '1085734', '1479920', '43300', '1338949', '1443799', '923473', '895642', '31235', '859475', '6201', '1095996', '935724', '216039', '940510', '1105055', '1329069']
---------------------------
821483
----------------------------
Report of Independent Registered Public Accounting Firm  The Board of Directors and Stockholders  Delta Petroleum Corporation:  We have audited the accompanying consolidated balance sheets of Delta Petroleum Corporation and subsidiaries as of December 31, 2010, and 2009, and the related consolidated statements of operations, changes in stockholders equity and comprehensive income (loss), and cash flows for each of the years in the three year period ended December 31, 2010. These consolidated financial statements are the responsibility of the Companys management. Our responsibility is to express an opinion on these consolidated financial statements based on our audits.  We conducted our audits in accordance with the standards of 

In [19]:
if 'yi_model' in locals() and yi_model is not None:
    del yi_model
    del yi_tokenizer
    print("Yi model and tokenizer objects deleted.")

# 2. Explicitly run Python's garbage collector
# This forces Python to reclaim memory from deleted objects
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
# This is crucial for freeing up unused GPU memory that PyTorch might have reserved
torch.cuda.empty_cache()
print("CUDA cache emptied.")


Python garbage collector run.
CUDA cache emptied.


In [20]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [21]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [22]:
device_map_balanced_yi = {
    'model.embed_tokens': 0, # Keep on GPU0
}


for i in range(22): 
    device_map_balanced_yi[f'model.layers.{i}'] = 0


for i in range(22, 48): 
    device_map_balanced_yi[f'model.layers.{i}'] = 1

device_map_balanced_yi.update({
    'model.norm': 1,
    'model.rotary_emb': 1, # Assuming Yi uses a rotary_emb module similar to Llama/DeepSeek
    'lm_head': 1,
})


# --- Model and Tokenizer Names for Yi-1.5-9B-Chat ---
yi_model_name = "01-ai/Yi-1.5-9B-Chat"

# Step 1: Load config for Yi
yi_config = AutoConfig.from_pretrained(yi_model_name)

# Step 2: Initialize empty model (using the corrected config which is now for 48 layers)
with init_empty_weights():
    yi_model = AutoModelForCausalLM.from_config(yi_config)

# Use the specific device map for Yi
yi_device_map = device_map_balanced_yi

# Step 3: Load pretrained weights with device_map
print(f"Loading {yi_model_name} with torch_dtype=torch.float16 and custom device_map...")
print(f"Device Map being used: {yi_device_map}")
yi_model = AutoModelForCausalLM.from_pretrained(
    yi_model_name,
    device_map=yi_device_map,
    torch_dtype=torch.float16, # Explicitly using float16 as requested
    low_cpu_mem_usage=True # Helps manage memory during loading
)
print(f"{yi_model_name} loaded successfully across GPUs.")

config.json:   0%|          | 0.00/661 [00:00<?, ?B/s]

Loading 01-ai/Yi-1.5-9B-Chat with torch_dtype=torch.float16 and custom device_map...
Device Map being used: {'model.embed_tokens': 0, 'model.layers.0': 0, 'model.layers.1': 0, 'model.layers.2': 0, 'model.layers.3': 0, 'model.layers.4': 0, 'model.layers.5': 0, 'model.layers.6': 0, 'model.layers.7': 0, 'model.layers.8': 0, 'model.layers.9': 0, 'model.layers.10': 0, 'model.layers.11': 0, 'model.layers.12': 0, 'model.layers.13': 0, 'model.layers.14': 0, 'model.layers.15': 0, 'model.layers.16': 0, 'model.layers.17': 0, 'model.layers.18': 0, 'model.layers.19': 0, 'model.layers.20': 0, 'model.layers.21': 0, 'model.layers.22': 1, 'model.layers.23': 1, 'model.layers.24': 1, 'model.layers.25': 1, 'model.layers.26': 1, 'model.layers.27': 1, 'model.layers.28': 1, 'model.layers.29': 1, 'model.layers.30': 1, 'model.layers.31': 1, 'model.layers.32': 1, 'model.layers.33': 1, 'model.layers.34': 1, 'model.layers.35': 1, 'model.layers.36': 1, 'model.layers.37': 1, 'model.layers.38': 1, 'model.layers.39':

model.safetensors.index.json: 0.00B [00:00, ?B/s]

Fetching 4 files:   0%|          | 0/4 [00:00<?, ?it/s]

model-00002-of-00004.safetensors:   0%|          | 0.00/4.98G [00:00<?, ?B/s]

...

model-00004-of-00004.safetensors:   0%|          | 0.00/2.78G [00:00<?, ?B/s]

model-00001-of-00004.safetensors:   0%|          | 0.00/4.93G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/132 [00:00<?, ?B/s]

01-ai/Yi-1.5-9B-Chat loaded successfully across GPUs.


In [23]:

# --- Load the tokenizer for the Yi model ---
# This assumes 'yi_model_name' is defined earlier, e.g., yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_tokenizer = AutoTokenizer.from_pretrained(yi_model_name)

# Set pad_token_id if it's not defined, crucial for generation
if yi_tokenizer.pad_token_id is None:
    yi_tokenizer.pad_token_id = yi_tokenizer.eos_token_id

tokenizer_config.json: 0.00B [00:00, ?B/s]

tokenizer.model:   0%|          | 0.00/1.03M [00:00<?, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

special_tokens_map.json:   0%|          | 0.00/567 [00:00<?, ?B/s]

In [24]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [25]:
# --- Paraphrase Function ---
def paraphrase_batch_yi(text_with_prompt, seeds, temps, token_count_input):
    results = []

    messages = [
        {"role": "user", "content": f"Original:\n{text_with_prompt}\n\n{paraphrase_instruction}"},
    ]

    final_yi_prompt = yi_tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        torch.manual_seed(seed)
        inputs = yi_tokenizer(final_yi_prompt, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}

        outputs = yi_model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=yi_tokenizer.eos_token_id,
            pad_token_id=yi_tokenizer.pad_token_id
        )

        decoded = yi_tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")
        print ('------------------------------------------------------')
        print ('\n')
        paraphrased_text = None

       # Step 1: Try matching up to newline followed by caret (\n^)
        match = re.search(r"<\|im_start\|> assistant\s*(.*?)(?:\n\^)", decoded, re.DOTALL)
        
        if match:
            paraphrased_text = match.group(1).strip()
        else:
            # Step 2: No \n^ found — find all carets
            assistant_start = re.search(r"<\|im_start\|> assistant\s*", decoded)
            if assistant_start:
                start_idx = assistant_start.end()
                post_assistant = decoded[start_idx:]
        
                caret_matches = list(re.finditer(r"\^", post_assistant))
        
                if len(caret_matches) >= 2:
                    # Capture text between start and second caret
                    paraphrased_text = post_assistant[:caret_matches[1].start()].strip()
                else:
                    # Step 3: Fallback — capture everything
                    paraphrased_text = post_assistant.strip()
        # Output result
        if paraphrased_text:
            print ('------------------------------------------------------')
            print ('\n')
            print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
            print(paraphrased_text)
            print(f"--- End MODIFIED OUTPUT for Attempt {i+1}  {model_small} ---\n")
            print ('------------------------------------------------------')
            print ('\n')
        else:
            print ('------------------------------------------------------')
            print ('\n')
            print("No match found.")
            print ('------------------------------------------------------')
            print ('\n')
        

        
        
        results.append(paraphrased_text)

    return results

In [26]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(yi_tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_yi(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

GPU Utilization:   0%|          | 0% , GPU0: 0%/7883MB | GPU1: 0%/9187MB


📄 Processing CIK: 821483
----------------------------------------------



CIK NUMBER: 821483



Original AUDIT OPTINION: 
Report of Independent Registered Public Accounting Firm  The Board of Directors and Stockholders  Delta Petroleum Corporation:  We have audited the accompanying consolidated balance sheets of Delta Petroleum Corporation and subsidiaries as of December 31, 2010, and 2009, and the related consolidated statements of operations, changes in stockholders equity and comprehensive income (loss), and cash flows for each of the years in the three year period ended December 31, 2010. These consolidated financial statements are the responsibility of the Companys management. Our responsibility is to express an opinion on these consolidated financial statements based on our audits.  We conducted our audits in accordance with the standards of the Public Company Accounting Oversight Board (United States). Those standards require that we plan and perform the audit to obtain reas

GPU Utilization:   0%|          | 0% , GPU0: 18%/8079MB | GPU1: 15%/9403MB

GPU Utilization:   0%|          | 0% , GPU0: 52%/8079MB | GPU1: 47%/9403MB

GPU Utilization:   0%|          | 0% , GPU0: 39%/8079MB | GPU1: 52%/9403MB

...

GPU Utilization:   0%|          | 0% , GPU0: 36%/8943MB | GPU1: 45%/10299MB

GPU Utilization:   0%|          | 0% , GPU0: 45%/8943MB | GPU1: 52%/10299MB

GPU Utilization:   0%|          | 0% , GPU0: 42%/8943MB | GPU1: 61%/10299MB

--- RAW LLM Output for Attempt 6 ---
<|im_start|> user
 Original:
 REPORT OF INDEPENDENT REGISTERED PUBLIC ACCOUNTING FIRM<p> To the Board of Directors and Stockholder of NewPage Corporation:<p> In our opinion,  the accompanying consolidated balance sheets and the related consolidated statements of operations,  equity (deficit) and cash flows present fairly,  in all material respects,  the financial position of NewPage Corporation and its subsidiaries at December 31,  2010  and 2009,  and the results of their operations and their cash flows for each of the three years in the period ended December 31,  2010  in conformity with accounting principles generally accepted in the United States of America.  These financial statements are the responsibility of the Companys management.  Our responsibility is to express an opinion on these financial statements based on our audits.  We conducted our audits of these statements in accordance with the standards of the Public Company Accounting Overs

GPU Utilization:   0%|          | 0% , GPU0: 42%/8943MB | GPU1: 61%/10299MB


In [27]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

✅ Master ZIP created with flat structure: /kaggle/working/2010_YI_ALL_PARAPHRASED.zip


/kaggle/working/2010_YI_ALL_PARAPHRASED.zip

# 2011

In [10]:
year=2011

In [11]:
dataset_path = '/kaggle/input/bankruptcies-audit-opinion/AUDIT_OPINION_ITEM_7_ONLY_YES_BANKRUPTCY/YES_BANKRUPTCY/'
dataset_path+=str(year)+'/'
print(os.listdir(dataset_path))
for cik in os.listdir(dataset_path):
    print ('---------------------------')
    print (cik)
    print ('----------------------------')
    audit_text_cik=dataset_path+cik+'/audit_opinion.txt'
    try:
        with open(audit_text_cik, 'r', encoding='utf-8') as f:
            content = f.read()
            print (content)
    except Exception as e:
        print(f"Error reading {audit_text_cik}: {e}")
    print ('///////////////////////////////////')

['1123541', '930835', '75208', '1167178', '840264', '1396426', '911002', '731859', '1376812', '1401106', '1120830', '314606', '32878', '1123647', '58361', '1104358', '724742', '1268984']
---------------------------
1123541
----------------------------
Report of independent registered public accounting firm<p>Board of Directors and Stockholders<p>Penson Worldwide, Inc.<p>Dallas, Texas<p>We have audited the accompanying consolidated statements of financial condition of Penson Worldwide, Inc. (the âCompanyâ) as of December 31, 2011 and 2010 and the related consolidated statements of operations, stockholdersâ equity, and cash flows for each of the three years in the period ended December 31, 2011. These financial statements are the responsibility of the Companyâs management. Our responsibility is to express an opinion on these financial statements based on our audits.<p>We conducted our audits in accordance with the standards of the Public Company Accounting Oversight Board (United

In [12]:
if 'yi_model' in locals() and yi_model is not None:
    del yi_model
    del yi_tokenizer
    print("Yi model and tokenizer objects deleted.")

# 2. Explicitly run Python's garbage collector
# This forces Python to reclaim memory from deleted objects
gc.collect()
print("Python garbage collector run.")

# 3. Release PyTorch's cached memory to the GPU driver
# This is crucial for freeing up unused GPU memory that PyTorch might have reserved
torch.cuda.empty_cache()
print("CUDA cache emptied.")


Python garbage collector run.
CUDA cache emptied.


In [13]:
!export PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True


In [14]:
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"


In [15]:
device_map_balanced_yi = {
    'model.embed_tokens': 0, # Keep on GPU0
}


for i in range(22): 
    device_map_balanced_yi[f'model.layers.{i}'] = 0


for i in range(22, 48): 
    device_map_balanced_yi[f'model.layers.{i}'] = 1

device_map_balanced_yi.update({
    'model.norm': 1,
    'model.rotary_emb': 1, # Assuming Yi uses a rotary_emb module similar to Llama/DeepSeek
    'lm_head': 1,
})


# --- Model and Tokenizer Names for Yi-1.5-9B-Chat ---
yi_model_name = "01-ai/Yi-1.5-9B-Chat"

# Step 1: Load config for Yi
yi_config = AutoConfig.from_pretrained(yi_model_name)

# Step 2: Initialize empty model (using the corrected config which is now for 48 layers)
with init_empty_weights():
    yi_model = AutoModelForCausalLM.from_config(yi_config)

# Use the specific device map for Yi
yi_device_map = device_map_balanced_yi

# Step 3: Load pretrained weights with device_map
print(f"Loading {yi_model_name} with torch_dtype=torch.float16 and custom device_map...")
print(f"Device Map being used: {yi_device_map}")
yi_model = AutoModelForCausalLM.from_pretrained(
    yi_model_name,
    device_map=yi_device_map,
    torch_dtype=torch.float16, # Explicitly using float16 as requested
    low_cpu_mem_usage=True # Helps manage memory during loading
)
print(f"{yi_model_name} loaded successfully across GPUs.")

config.json:   0%|          | 0.00/661 [00:00<?, ?B/s]

Loading 01-ai/Yi-1.5-9B-Chat with torch_dtype=torch.float16 and custom device_map...
Device Map being used: {'model.embed_tokens': 0, 'model.layers.0': 0, 'model.layers.1': 0, 'model.layers.2': 0, 'model.layers.3': 0, 'model.layers.4': 0, 'model.layers.5': 0, 'model.layers.6': 0, 'model.layers.7': 0, 'model.layers.8': 0, 'model.layers.9': 0, 'model.layers.10': 0, 'model.layers.11': 0, 'model.layers.12': 0, 'model.layers.13': 0, 'model.layers.14': 0, 'model.layers.15': 0, 'model.layers.16': 0, 'model.layers.17': 0, 'model.layers.18': 0, 'model.layers.19': 0, 'model.layers.20': 0, 'model.layers.21': 0, 'model.layers.22': 1, 'model.layers.23': 1, 'model.layers.24': 1, 'model.layers.25': 1, 'model.layers.26': 1, 'model.layers.27': 1, 'model.layers.28': 1, 'model.layers.29': 1, 'model.layers.30': 1, 'model.layers.31': 1, 'model.layers.32': 1, 'model.layers.33': 1, 'model.layers.34': 1, 'model.layers.35': 1, 'model.layers.36': 1, 'model.layers.37': 1, 'model.layers.38': 1, 'model.layers.39':

model.safetensors.index.json: 0.00B [00:00, ?B/s]

Fetching 4 files:   0%|          | 0/4 [00:00<?, ?it/s]

model-00004-of-00004.safetensors:   0%|          | 0.00/2.78G [00:00<?, ?B/s]

...

model-00002-of-00004.safetensors:   0%|          | 0.00/4.98G [00:00<?, ?B/s]

model-00003-of-00004.safetensors:   0%|          | 0.00/4.97G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/132 [00:00<?, ?B/s]

01-ai/Yi-1.5-9B-Chat loaded successfully across GPUs.


In [16]:

# --- Load the tokenizer for the Yi model ---
# This assumes 'yi_model_name' is defined earlier, e.g., yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_model_name = "01-ai/Yi-1.5-9B-Chat"
yi_tokenizer = AutoTokenizer.from_pretrained(yi_model_name)

# Set pad_token_id if it's not defined, crucial for generation
if yi_tokenizer.pad_token_id is None:
    yi_tokenizer.pad_token_id = yi_tokenizer.eos_token_id

tokenizer_config.json: 0.00B [00:00, ?B/s]

tokenizer.model:   0%|          | 0.00/1.03M [00:00<?, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

special_tokens_map.json:   0%|          | 0.00/567 [00:00<?, ?B/s]

In [17]:
# --- GPU Monitor Toggle ---
monitor_stop = False

# --- GPU Monitor Function ---
def gpu_monitor():
    with tqdm(total=100, desc="GPU Utilization", bar_format="{l_bar}{bar}| {n_fmt}% {postfix}") as pbar:
        while not monitor_stop:
            subprocess.run("clear", shell=True)
            result = subprocess.run(
                "nvidia-smi --query-gpu=utilization.gpu,memory.used --format=csv,noheader,nounits",
                capture_output=True, shell=True, text=True
            )
            gpu_data = result.stdout.strip().split('\n')
            gpu_info_str = []
            for i, line in enumerate(gpu_data):
                gpu_util, mem_used = line.replace(" %, ", " ").replace(", ", " ").split()
                gpu_info_str.append(f"GPU{i}: {gpu_util}%/{int(mem_used)}MB")
            pbar.set_postfix_str(" | ".join(gpu_info_str))
            pbar.update(0)
            time.sleep(2)

In [18]:
# --- Paraphrase Function ---
def paraphrase_batch_yi(text_with_prompt, seeds, temps, token_count_input):
    results = []

    messages = [
        {"role": "user", "content": f"Original:\n{text_with_prompt}\n\n{paraphrase_instruction}"},
    ]

    final_yi_prompt = yi_tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)
    input_device = "cuda:0"

    for i, (seed, temp) in enumerate(zip(seeds, temps)):
        torch.manual_seed(seed)
        inputs = yi_tokenizer(final_yi_prompt, return_tensors="pt")
        inputs = {k: v.to(input_device) for k, v in inputs.items()}

        outputs = yi_model.generate(
            **inputs,
            max_new_tokens=token_count_input + 3500,
            min_new_tokens=token_count_input - 20,
            temperature=temp,
            top_p=0.92,
            top_k=50,
            repetition_penalty=1.1,
            do_sample=True,
            eos_token_id=yi_tokenizer.eos_token_id,
            pad_token_id=yi_tokenizer.pad_token_id
        )

        decoded = yi_tokenizer.decode(outputs[0], skip_special_tokens=True)
        print(f"--- RAW LLM Output for Attempt {i+1} ---")
        print(decoded)
        print(f"--- End RAW LLM Output for Attempt {i+1} ---\n")
        print ('------------------------------------------------------')
        print ('\n')
        paraphrased_text = None

       # Step 1: Try matching up to newline followed by caret (\n^)
        match = re.search(r"<\|im_start\|> assistant\s*(.*?)(?:\n\^)", decoded, re.DOTALL)
        
        if match:
            paraphrased_text = match.group(1).strip()
        else:
            # Step 2: No \n^ found — find all carets
            assistant_start = re.search(r"<\|im_start\|> assistant\s*", decoded)
            if assistant_start:
                start_idx = assistant_start.end()
                post_assistant = decoded[start_idx:]
        
                caret_matches = list(re.finditer(r"\^", post_assistant))
        
                if len(caret_matches) >= 2:
                    # Capture text between start and second caret
                    paraphrased_text = post_assistant[:caret_matches[1].start()].strip()
                else:
                    # Step 3: Fallback — capture everything
                    paraphrased_text = post_assistant.strip()
        # Output result
        if paraphrased_text:
            print ('------------------------------------------------------')
            print ('\n')
            print(f"--- MODIFIED OUTPUT (Paraphrase Only) for Attempt {i+1} {model_small} ---")
            print(paraphrased_text)
            print(f"--- End MODIFIED OUTPUT for Attempt {i+1}  {model_small} ---\n")
            print ('------------------------------------------------------')
            print ('\n')
        else:
            print ('------------------------------------------------------')
            print ('\n')
            print("No match found.")
            print ('------------------------------------------------------')
            print ('\n')
        

        
        
        results.append(paraphrased_text)

    return results

In [19]:
# ΘΑ ΤΡΕΞΟΥΜΕ ΕΞΙ SEEDS ΓΙΑΤΙ ΘΑ ΚΑΝΟΥΜΕ MANUAL ΕΛΕΓΧΟ ΣΤΟ ΤΕΛΟΣ ΚΑΙ ΘΑ ΔΙΑΓΡΑΦΟΥΜΕ ΕΝΑ ΠΕΡΙΠΟΥ 5 % ΠΟΥ ΒΓΗΚΕ ΦΥΡΑ ΑΠΟ ΤΟ LLM

#--- Run for All CIKs in Year ---

# --- Create storage dictionary for one year ---
year_data = {}

# --- Seeds and temperatures for 6 paraphrases only ---
temps = [0.75 + 0.02 * i for i in range(6)]
seeds = list(range(1000, 1006))



monitor_thread = threading.Thread(target=gpu_monitor)
monitor_thread.start()

try:
    for cik in os.listdir(dataset_path):
        print(f"\n📄 Processing CIK: {cik}")
        audit_text_path = os.path.join(dataset_path, cik, "audit_opinion.txt")
        

        try:
            with open(audit_text_path, 'r', encoding='utf-8') as f:
                original_content = f.read()
        except Exception as e:
            print(f"⚠️ Error reading {audit_text_path}: {e}")
            continue

        token_count = len(yi_tokenizer.encode(original_content))
        print('----------------------------------------------')
        print('\n\n')
        print ('CIK NUMBER: '+cik)
        print("\n\n")
        print ("Original AUDIT OPTINION: \n"+original_content)
        print ("\n\n")
        print(f"Token count of original audit opinion text: {token_count}")
        print(f"Word count of original audit opinion text: {len(original_content.split())}")

        max_retries = 4
        retry_wait = 15  # seconds
        
        for attempt in range(1, max_retries + 1):
            try:
                paraphrases = paraphrase_batch_yi(original_content, seeds, temps, token_count)
                break  # Success, exit retry loop
            except RuntimeError as e:
                if "CUDA out of memory" in str(e):
                    print(f"🚨 CUDA OOM error on CIK {cik}, attempt {attempt}/{max_retries}")
                    torch.cuda.empty_cache()
                    time.sleep(retry_wait)
                    continue
                else:
                    print(f"🚨 Non-CUDA error paraphrasing CIK {cik}: {e}")
                    break  # Don't retry for non-CUDA errors
            except Exception as e:
                print(f"🚨 Unexpected error paraphrasing CIK {cik}: {e}")
                break
        else:
            print(f"❌ Failed to paraphrase CIK {cik} after {max_retries} retries due to CUDA OOM")
            continue  # Skip this CIK if all retries failed

        # Build dictionary for this CIK
        cik_entry = {"original": original_content}
        for i, p in enumerate(paraphrases):
            cik_entry[f"paraphrase_{i+1}"] = p

        year_data[cik] = cik_entry
        
        # --- Create output folder and ZIP the paraphrases ---
        output_dir = os.path.join(str(year), cik, "PARAPHRASED_AUDITS", model_full)
        os.makedirs(output_dir, exist_ok=True)
        # Write paraphrases to .txt files
        txt_files = []
        for i, paraphrase in enumerate(paraphrases, 1):
            file_path = os.path.join(output_dir, f"paraphrase_{i}.txt")
            with open(file_path, "w", encoding="utf-8") as f:
                f.write(paraphrase)
            txt_files.append(file_path)
        
        print(f"✅ Paraphrased files written for CIK {cik} at: {output_dir}")
        for file in txt_files:
            print(f"   └─ {file}")
        print('--------------------------------------------')
        print('\n\n\n\n\n\n')

finally:
    monitor_stop = True
    if monitor_thread.is_alive():
        monitor_thread.join()

GPU Utilization:   0%|          | 0% , GPU0: 0%/7883MB | GPU1: 0%/9187MB


📄 Processing CIK: 1123541
----------------------------------------------



CIK NUMBER: 1123541



Original AUDIT OPTINION: 
Report of independent registered public accounting firm<p>Board of Directors and Stockholders<p>Penson Worldwide, Inc.<p>Dallas, Texas<p>We have audited the accompanying consolidated statements of financial condition of Penson Worldwide, Inc. (the âCompanyâ) as of December 31, 2011 and 2010 and the related consolidated statements of operations, stockholdersâ equity, and cash flows for each of the three years in the period ended December 31, 2011. These financial statements are the responsibility of the Companyâs management. Our responsibility is to express an opinion on these financial statements based on our audits.<p>We conducted our audits in accordance with the standards of the Public Company Accounting Oversight Board (United States). Those standards require that we plan and perform the audit to obtain reasonable assurance about whether the financia

GPU Utilization:   0%|          | 0% , GPU0: 1%/8029MB | GPU1: 23%/9345MB

GPU Utilization:   0%|          | 0% , GPU0: 42%/8031MB | GPU1: 50%/9345MB

GPU Utilization:   0%|          | 0% , GPU0: 48%/8045MB | GPU1: 58%/9357MB

...

GPU Utilization:   0%|          | 0% , GPU0: 40%/8935MB | GPU1: 50%/10283MB

GPU Utilization:   0%|          | 0% , GPU0: 37%/8935MB | GPU1: 45%/10283MB

GPU Utilization:   0%|          | 0% , GPU0: 41%/8935MB | GPU1: 52%/10283MB

--- RAW LLM Output for Attempt 6 ---
<|im_start|> user
 Original:
 REPORT OF INDEPENDENT REGISTERED PUBLIC ACCOUNTING FIRM<p> To the Board of Directors and Stockholders of Reddy Ice Holdings,  Inc. :<p>         In our opinion,  the consolidated financial statements listed in the accompanying index present fairly,  in all material respects,  the financial position of Reddy Ice Holdings,  Inc.  and its subsidiary (the "Company") at December 31,  2011  and 2010,  and the results of their operations and their cash flows for each of the three years in the period ended December 31,  2011  in conformity with accounting principles generally accepted in the United States of America.  These financial statements are the responsibility of the Company's management.  Our responsibility is to express an opinion on these financial statements based on our audits.  We conducted our audits of these statements in accordance with the standards of the Public Company Accounting Oversight Board (United States

GPU Utilization:   0%|          | 0% , GPU0: 41%/8935MB | GPU1: 52%/10283MB


In [20]:
# Call it for current year 
master_zip = create_master_zip_flat(year)
display(FileLink(master_zip))

✅ Master ZIP created with flat structure: /kaggle/working/2011_YI_ALL_PARAPHRASED.zip


/kaggle/working/2011_YI_ALL_PARAPHRASED.zip